## Предсказание стоимости квартиры на основе геопараметров

Проверка влияния параметров городской инфраструктуры на стоимость квартир. Насколько велика эта добавочная стоимость.

Задание и данные указаны [здесь](https://ods.ai/competitions/geo_course_real_estate).

In [1]:
!pip -q install folium matplotlib mapclassify osmnx networkx

In [3]:
pip install osmnx

Note: you may need to restart the kernel to use updated packages.


In [4]:
pip install --upgrade pip

Note: you may need to restart the kernel to use updated packages.


In [368]:
pip install catboost

python3.9(84387) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.


  Using cached tenacity-9.0.0-py3-none-any.whl.metadata (1.2 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.1/27.1 MB 5.4 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.1/19.1 MB 6.9 MB/s eta 0:00:0000:0100:01
Using cached tenacity-9.0.0-py3-none-any.whl (28 kB)
Note: you may need to restart the kernel to use updated packages.


In [392]:
import pandas as pd
import numpy as np
import geopandas as gpd
import osmnx as ox
import networkx as nx

from shapely import wkt

from sklearn import metrics

from sklearn.model_selection import train_test_split
from sklearn.metrics import root_mean_squared_error
# Если колаб выдаёт ошибку при импорте метрики, перезагрузите среду выполнения
from catboost.utils import eval_metric
from catboost import CatBoostRegressor, Pool

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)

Задача заключается в предсказании стоимость квартир для тестового набора данных (*test.csv*) на основе геопризнаков. Такими параметрами были выбраны пешеходная доступность от квартиры до трамвайных остановок и станций метро.

Эти виды транспорта были выбраны в виду своих преимуществ перед другими видами городского общественного транспорта (вместимость, скорость, экологичность, отсутствие пробок).

In [6]:
# Считываем данные
df_train = pd.read_csv("df_train.csv", index_col=[0])
df_test = pd.read_csv("df_test.csv", index_col=[0])

In [7]:
df_train.head()

latitude  longitude       city  area  area_kitchen  rooms_num  has_balcony  \
0   53.2117    50.1669     Самара  33.9           8.0          1         True   
1   45.0389    39.0985  Краснодар  49.8          12.0          2         True   
2   45.0694    38.9716  Краснодар  45.1          25.1          2         True   
3   53.2164    50.2605     Самара  70.1          10.0          3         True   
4   53.1651    50.3842     Самара  34.0           NaN          1         True   

     price  
0  2473000  
1  3733000  
2  3445000  
3  4458000  
4  1295000

In [69]:
# Создаём колонку геометрий
df_train["geometry"] = gpd.points_from_xy(
    x=df_train["longitude"], y=df_train["latitude"], crs="EPSG:4326"
)
df_test["geometry"] = gpd.points_from_xy(
    x=df_test["longitude"], y=df_test["latitude"], crs="EPSG:4326"
)

In [70]:
df_train

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  
0            True  2473000  POINT (50.16690 53.21170)  
1            True  3733000  POINT (39.09850 45.03890)  
2            True  3445000  POINT (38.97160 45.06940)  
3            True  4458000  POINT (50.26050 53.21640)  
4            True  1295000  POINT (50.38420 53.16510)  
...           ...      ...                        ...  
8037         True  4029000  POINT (50.27850 53.23990)  
8038         True  5263000  POINT (38.96660 45.07390)  
8039        False  2017000  POINT (39.02880 45.11270)  
8040         True  5617000  POINT (39.01790 45.05130)  
8041         True  3729000  POINT (38.95250 45.10920)  

[8042 rows x 9 columns]

Создаём переменные с пешеходными графами городов

In [8]:
city_1 = ox.geocode_to_gdf(["Россия, Краснодар"])
polygon_1 = city_1.iloc[0]["geometry"]
G_krasnodar = ox.graph_from_polygon(polygon_1, network_type="walk", simplify=True)
G_krasnodar = ox.project_graph(G_krasnodar)
nodes_1, edges_1 = ox.graph_to_gdfs(G_krasnodar)

In [9]:
city_2 = ox.geocode_to_gdf(["Россия, город Нижний Новгород"])
polygon_2 = city_2.iloc[0]["geometry"]
G_nizhny_novgorod = ox.graph_from_polygon(polygon_2, network_type="walk", simplify=True)
G_nizhny_novgorod = ox.project_graph(G_nizhny_novgorod)
nodes_2, edges_2 = ox.graph_to_gdfs(G_nizhny_novgorod)

In [10]:
city_3 = ox.geocode_to_gdf(["Россия, Самара"])
polygon_3 = city_3.iloc[0]["geometry"]
G_samara = ox.graph_from_polygon(polygon_3, network_type="walk", simplify=True)
G_samara = ox.project_graph(G_samara)
nodes_3, edges_3 = ox.graph_to_gdfs(G_samara)

In [11]:
# Проверим какая система координат сейчас
nodes_1.crs

<Projected CRS: EPSG:32637>
Name: WGS 84 / UTM zone 37N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 36°E and 42°E, northern hemisphere between equator and 84°N, onshore and offshore. Djibouti. Egypt. Eritrea. Ethiopia. Georgia. Iraq. Jordan. Kenya. Lebanon. Russian Federation. Saudi Arabia. Somalia. Sudan. Syria. Türkiye (Turkey). Ukraine.
- bounds: (36.0, 0.0, 42.0, 84.0)
Coordinate Operation:
- name: UTM zone 37N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [12]:
edges_1.crs

<Projected CRS: EPSG:32637>
Name: WGS 84 / UTM zone 37N
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Between 36°E and 42°E, northern hemisphere between equator and 84°N, onshore and offshore. Djibouti. Egypt. Eritrea. Ethiopia. Georgia. Iraq. Jordan. Kenya. Lebanon. Russian Federation. Saudi Arabia. Somalia. Sudan. Syria. Türkiye (Turkey). Ukraine.
- bounds: (36.0, 0.0, 42.0, 84.0)
Coordinate Operation:
- name: UTM zone 37N
- method: Transverse Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [13]:
# Выгружаем остановки общественного транспорта в городах из OpenStreetMap
tags = {"public_transport": True}

features_krasnodar = ox.features.features_from_place("Krasnodar", tags=tags)
features_krasnodar = features_krasnodar.dropna(subset=["name"]) # дополнительно удаляем остановки без названий

In [14]:
features_krasnodar.head()

name public_transport railway train  \
element_type osmid                                                           
node         295153970   Завод имени Седина    stop_position    stop   yes   
             295154027                  МЖК    stop_position    stop   yes   
             295154538  улица Автолюбителей    stop_position     NaN   NaN   
             295155338               ВНИИМК    stop_position     NaN   NaN   
             295155923    Тургеневский мост         platform     NaN   NaN   

                                         geometry  bus bench  bin   highway  \
element_type osmid                                                            
node         295153970  POINT (38.96748 45.00571)  NaN   NaN  NaN       NaN   
             295154027  POINT (39.00583 45.02738)  NaN   NaN  NaN       NaN   
             295154538  POINT (39.06658 45.00647)  yes   NaN  NaN       NaN   
             295155338  POINT (39.01388 45.03433)  yes   NaN  NaN       NaN   
             295155923  POINT (38.95281 45.03714)  NaN   yes  yes  bus_stop   

                        lit  ... nodes addr:city addr:housenumber building  \
element_type osmid           ...                                             
node         295153970  NaN  ...   NaN       NaN              NaN      NaN   
             295154027  NaN  ...   NaN       NaN              NaN      NaN   
             295154538  NaN  ...   NaN       NaN              NaN      NaN   
             295155338  NaN  ...   NaN       NaN              NaN      NaN   
             295155923  yes  ...   NaN       NaN              NaN      NaN   

                       building:levels opening_hours website area ways type  
element_type osmid                                                           
node         295153970             NaN           NaN     NaN  NaN  NaN  NaN  
             295154027             NaN           NaN     NaN  NaN  NaN  NaN  
             295154538             NaN           NaN     NaN  NaN  NaN  NaN  
             295155338             NaN           NaN     NaN  NaN  NaN  NaN  
             295155923             NaN           NaN     NaN  NaN  NaN  NaN  

[5 rows x 53 columns]

In [15]:
# Оставляем только трамвайные остановки и станции метро (в случае с Краснодаром без остановок метро)
stops_krasnodar = features_krasnodar[features_krasnodar.tram.notnull()]
stops_krasnodar.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 414 entries, ('node', 295156463) to ('way', 1147746640)
Data columns (total 53 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   name                           414 non-null    object  
 1   public_transport               414 non-null    object  
 2   railway                        368 non-null    object  
 3   train                          0 non-null      object  
 4   geometry                       414 non-null    geometry
 5   bus                            1 non-null      object  
 6   bench                          127 non-null    object  
 7   bin                            20 non-null     object  
 8   highway                        2 non-null      object  
 9   lit                            8 non-null      object  
 10  shelter                        129 non-null    object  
 11  tactile_paving                 15 non-null     object  

In [16]:
# С помощью модуля representative_point уточняем точки внутри полигонов или линий, которыми могут быть
# обозначены остановки
stops_krasnodar["geometry"] = stops_krasnodar["geometry"].representative_point()
stops_krasnodar = stops_krasnodar[["name", "geometry"]]

stops_krasnodar.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 414 entries, ('node', 295156463) to ('way', 1147746640)
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   name      414 non-null    object  
 1   geometry  414 non-null    geometry
dtypes: geometry(1), object(1)
memory usage: 88.1+ KB


/Users/andrey/.pyenv/versions/3.9.0/lib/python3.9/site-packages/geopandas/geodataframe.py:1528: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [26]:
# Переводим геометрию точек в корректную проекцию города, определённую ранее
stops_krasnodar_crs = (
    stops_krasnodar
    .to_crs(edges_1.crs)
)

In [27]:
# Добавляем столбец "nearest_node", куда будут добавляться ближайшие узлы графа OpenStreetMap
# к координатам, чтобы в дальнейшем по ним можно было найти кратчайший маршрут
stops_krasnodar_crs["nearest_node"] = ""

In [28]:
stops_krasnodar_crs

name  \
element_type osmid                                  
node         295156463              Западное депо   
             295165788     Железнодорожный вокзал   
             494313596             улица Тульская   
             527253318       Индустриальная улица   
             583240123              улица Минская   
...                                           ...   
way          1147746625          Гомельская улица   
             1147746626           Ахтарская улица   
             1147746627           Ахтарская улица   
             1147746639  улица Петра Метальникова   
             1147746640  улица Петра Метальникова   

                                               geometry nearest_node  
element_type osmid                                                    
node         295156463   POINT (493995.116 4990515.645)               
             295165788   POINT (499139.634 4985157.345)               
             494313596   POINT (494456.271 4987148.925)               
             527253318   POINT (497057.716 4982953.622)               
             583240123   POINT (494817.846 4987356.667)               
...                                                 ...          ...  
way          1147746625  POINT (500121.254 4992263.498)               
             1147746626  POINT (500150.683 4992803.314)               
             1147746627  POINT (500145.731 4992898.750)               
             1147746639  POINT (500184.679 4993309.325)               
             1147746640  POINT (500179.068 4993340.097)               

[414 rows x 3 columns]

In [29]:
# Устанавливаем столбец "name" в качестве индекса датафрейма, чтобы к датасету можно было обращаться по меткам
stops_krasnodar_crs = stops_krasnodar_crs.set_index("name")

In [30]:
# С помощью библиотеки osmnx ищем ближайшие узлы графа OpenStreetMap для координат
# остановочных пунктов в городе
stops_krasnodar_crs["nearest_node"] = stops_krasnodar_crs["geometry"].apply(
    lambda x: ox.distance.nearest_nodes(G_krasnodar, x.x, x.y)
)

In [31]:
stops_krasnodar_crs

geometry  nearest_node
name                                                                  
Западное депо             POINT (493995.116 4990515.645)    1992135309
Железнодорожный вокзал    POINT (499139.634 4985157.345)     484799395
улица Тульская            POINT (494456.271 4987148.925)    1042862412
Индустриальная улица      POINT (497057.716 4982953.622)    1999275090
улица Минская             POINT (494817.846 4987356.667)     909333085
...                                                  ...           ...
Гомельская улица          POINT (500121.254 4992263.498)    9630264591
Ахтарская улица           POINT (500150.683 4992803.314)    1959404003
Ахтарская улица           POINT (500145.731 4992898.750)    1999164662
улица Петра Метальникова  POINT (500184.679 4993309.325)   10679233676
улица Петра Метальникова  POINT (500179.068 4993340.097)   10679281412

[414 rows x 2 columns]

In [32]:
stops_krasnodar_crs.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 414 entries, Западное депо to улица Петра Метальникова
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   geometry      414 non-null    geometry
 1   nearest_node  414 non-null    int64   
dtypes: geometry(1), int64(1)
memory usage: 9.7+ KB


In [33]:
# Сохраняем датафрейм с остановками в Краснодаре в csv-файл
stops_krasnodar_crs.to_csv("stops_krasnodar_crs.csv")

In [38]:
# Выгружаем остановки общественного транспорта в городах из OpenStreetMap
tags = {"public_transport": True}

features_nizhny = ox.features.features_from_place("Nizhny Novgorod", tags=tags)
features_nizhny = features_nizhny.dropna(subset=["name"])

features_nizhny.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 3009 entries, ('node', 76481133) to ('relation', 8455183)
Data columns (total 78 columns):
 #   Column                                       Non-Null Count  Dtype   
---  ------                                       --------------  -----   
 0   bus                                          1648 non-null   object  
 1   name                                         3009 non-null   object  
 2   public_transport                             3009 non-null   object  
 3   share_taxi                                   827 non-null    object  
 4   geometry                                     3009 non-null   geometry
 5   trolleybus                                   532 non-null    object  
 6   railway                                      448 non-null    object  
 7   train                                        79 non-null     object  
 8   network                                      28 non-null     object  
 9   operator             

In [39]:
# Оставляем только трамвайные остановки и станции метро
# С помощью конкатенации собираем их вместе в новый датафрейм
stops_nizhny = pd.concat([
    features_nizhny[features_nizhny.tram.notnull()],
    features_nizhny[features_nizhny.station.notnull()]
])

stops_nizhny.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 578 entries, ('node', 324688711) to ('node', 5584606667)
Data columns (total 78 columns):
 #   Column                                       Non-Null Count  Dtype   
---  ------                                       --------------  -----   
 0   bus                                          35 non-null     object  
 1   name                                         578 non-null    object  
 2   public_transport                             578 non-null    object  
 3   share_taxi                                   3 non-null      object  
 4   geometry                                     578 non-null    geometry
 5   trolleybus                                   16 non-null     object  
 6   railway                                      333 non-null    object  
 7   train                                        0 non-null      object  
 8   network                                      14 non-null     object  
 9   operator              

In [40]:
# С помощью модуля representative_point уточняем точки внутри полигонов или линий, которыми могут быть
# обозначены остановки
stops_nizhny["geometry"] = stops_nizhny["geometry"].representative_point()
stops_nizhny = stops_nizhny[["name", "geometry"]]

stops_nizhny.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 578 entries, ('node', 324688711) to ('node', 5584606667)
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   name      578 non-null    object  
 1   geometry  578 non-null    geometry
dtypes: geometry(1), object(1)
memory usage: 99.9+ KB


In [41]:
# Переводим геометрию точек в корректную проекцию города, определённую ранее
stops_nizhny_crs = (
    stops_nizhny
    .to_crs(edges_2.crs)
)

In [42]:
stops_nizhny_crs.head()

name                        geometry
element_type osmid                                                           
node         324688711   Красносельская улица  POINT (437059.380 6240885.304)
             359142331              Универмаг  POINT (429650.304 6233648.133)
             359143737  Троллейбусное депо №3  POINT (432360.789 6235826.898)
             359143826         Игарская улица  POINT (431682.606 6237896.841)
             479501580      улица Добролюбова  POINT (437777.901 6242650.618)

In [43]:
# Добавляем столбец "nearest_node", куда будут добавляться ближайшие узлы графа OpenStreetMap
# к координатам, чтобы в дальнейшем по ним можно было найти кратчайший маршрут
stops_nizhny_crs["nearest_node"] = ""

In [44]:
# Устанавливаем столбец "name" в качестве индекса датафрейма, чтобы к датасету можно было обращаться по меткам
stops_nizhny_crs = stops_nizhny_crs.set_index("name")

In [46]:
# С помощью библиотеки osmnx ищем ближайшие узлы графа OpenStreetMap для координат
# остановочных пунктов в городе
stops_nizhny_crs["nearest_node"] = stops_nizhny_crs["geometry"].apply(
    lambda x: ox.distance.nearest_nodes(G_nizhny_novgorod, x.x, x.y)
)

In [47]:
stops_nizhny_crs.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 578 entries, Красносельская улица to Стрелка
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   geometry      578 non-null    geometry
 1   nearest_node  578 non-null    int64   
dtypes: geometry(1), int64(1)
memory usage: 13.5+ KB


In [48]:
# Сохраняем датафрейм с остановками в Нижнем Новгороде в csv-файл
stops_nizhny_crs.to_csv("stops_nizhny_crs.csv")

In [49]:
# Выгружаем остановки общественного транспорта в городах из OpenStreetMap
tags = {"public_transport": True}

features_samara = ox.features.features_from_place("Samara", tags=tags)
features_samara = features_samara.dropna(subset=["name"])

features_samara.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 2449 entries, ('node', 143971493) to ('way', 1314024300)
Data columns (total 63 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   highway                        128 non-null    object  
 1   ref                            6 non-null      object  
 2   geometry                       2449 non-null   geometry
 3   bus                            943 non-null    object  
 4   name                           2449 non-null   object  
 5   public_transport               2449 non-null   object  
 6   trolleybus                     217 non-null    object  
 7   railway                        121 non-null    object  
 8   tram                           302 non-null    object  
 9   merkator_shift:bing            2 non-null      object  
 10  crossing                       2 non-null      object  
 11  tactile_paving                 165 non-null    object 

In [50]:
# Оставляем только трамвайные остановки и станции метро
# С помощью конкатенации собираем их вместе в новый датафрейм
stops_samara = pd.concat([
    features_samara[features_samara.tram.notnull()],
    features_samara[features_samara.station.notnull()]
])

stops_samara.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
MultiIndex: 310 entries, ('node', 152340065) to ('node', 3779454539)
Data columns (total 63 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   highway                        1 non-null      object  
 1   ref                            0 non-null      object  
 2   geometry                       310 non-null    geometry
 3   bus                            21 non-null     object  
 4   name                           310 non-null    object  
 5   public_transport               310 non-null    object  
 6   trolleybus                     0 non-null      object  
 7   railway                        52 non-null     object  
 8   tram                           302 non-null    object  
 9   merkator_shift:bing            1 non-null      object  
 10  crossing                       0 non-null      object  
 11  tactile_paving                 7 non-null      object 

In [51]:
# В датасете Самары оказалось только 8 станций местного метрополитена из 10 ныне действующих,
# поэтому добавим оставшиеся 2 станции вручную
df_stops_lost = pd.DataFrame(
    {
        "name": ["Юнгородок", "Кировская"],
        "Latitude": [50.2825, 50.26963],
        "Longitude": [53.2125, 53.211348],
        "station": ["yes", "yes"]
    }
)

In [52]:
# Из датафрейма делаем геодатафрейм
gdf_stops_lost = gpd.GeoDataFrame(
    df_stops_lost, geometry=gpd.points_from_xy(df_stops_lost.Latitude, df_stops_lost.Longitude), crs="EPSG:4326"
)

In [53]:
gdf_stops_lost.head()

name  Latitude  Longitude station                   geometry
0  Юнгородок  50.28250  53.212500     yes  POINT (50.28250 53.21250)
1  Кировская  50.26963  53.211348     yes  POINT (50.26963 53.21135)

In [54]:
# Добавляем 2 недостающие станции метро в общий датафрейм с трамвайными остановками и станциями метро в Самаре
stops_samara = pd.concat([stops_samara, gdf_stops_lost], ignore_index= True)

stops_samara.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 312 entries, 0 to 311
Data columns (total 65 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   highway                        1 non-null      object  
 1   ref                            0 non-null      object  
 2   geometry                       312 non-null    geometry
 3   bus                            21 non-null     object  
 4   name                           312 non-null    object  
 5   public_transport               310 non-null    object  
 6   trolleybus                     0 non-null      object  
 7   railway                        52 non-null     object  
 8   tram                           302 non-null    object  
 9   merkator_shift:bing            1 non-null      object  
 10  crossing                       0 non-null      object  
 11  tactile_paving                 7 non-null      object  
 12  share_taxi                  

In [55]:
# Проверяем станцим самарского метрополитена и смотрим их количество
stops_samara[stops_samara.station.notnull()]

highway  ref                   geometry  bus         name  \
302     NaN  NaN  POINT (50.24844 53.21284)  NaN    Безымянка   
303     NaN  NaN  POINT (50.23577 53.20698)  NaN       Победа   
304     NaN  NaN  POINT (50.22044 53.20155)  NaN    Советская   
305     NaN  NaN  POINT (50.19958 53.20096)  NaN   Спортивная   
306     NaN  NaN  POINT (50.17651 53.20027)  NaN  Гагаринская   
307     NaN  NaN  POINT (50.16050 53.20281)  NaN   Московская   
308     NaN  NaN  POINT (50.14899 53.21192)  NaN   Российская   
309     NaN  NaN  POINT (50.13420 53.20958)  NaN   Алабинская   
310     NaN  NaN  POINT (50.28250 53.21250)  NaN    Юнгородок   
311     NaN  NaN  POINT (50.26963 53.21135)  NaN    Кировская   

    public_transport trolleybus  railway tram merkator_shift:bing  ...  \
302         platform        NaN  station  NaN                 NaN  ...   
303         platform        NaN  station  NaN                 NaN  ...   
304         platform        NaN  station  NaN                 NaN  ...   
305         platform        NaN  station  NaN                 NaN  ...   
306         platform        NaN  station  NaN                 NaN  ...   
307         platform        NaN  station  NaN                 NaN  ...   
308         platform        NaN  station  NaN                 NaN  ...   
309         platform        NaN  station  NaN                 NaN  ...   
310              NaN        NaN      NaN  NaN                 NaN  ...   
311              NaN        NaN      NaN  NaN                 NaN  ...   

    passenger_information_display building:colour natural type  \
302                           NaN             NaN     NaN  NaN   
303                           NaN             NaN     NaN  NaN   
304                           NaN             NaN     NaN  NaN   
305                           NaN             NaN     NaN  NaN   
306                           NaN             NaN     NaN  NaN   
307                           NaN             NaN     NaN  NaN   
308                           NaN             NaN     NaN  NaN   
309                           NaN             NaN     NaN  NaN   
310                           NaN             NaN     NaN  NaN   
311                           NaN             NaN     NaN  NaN   

    departures_board addr:housenumber addr:street ways  Latitude  Longitude  
302              NaN              NaN         NaN  NaN       NaN        NaN  
303              NaN              NaN         NaN  NaN       NaN        NaN  
304              NaN              NaN         NaN  NaN       NaN        NaN  
305              NaN              NaN         NaN  NaN       NaN        NaN  
306              NaN              NaN         NaN  NaN       NaN        NaN  
307              NaN              NaN         NaN  NaN       NaN        NaN  
308              NaN              NaN         NaN  NaN       NaN        NaN  
309              NaN              NaN         NaN  NaN       NaN        NaN  
310              NaN              NaN         NaN  NaN  50.28250  53.212500  
311              NaN              NaN         NaN  NaN  50.26963  53.211348  

[10 rows x 65 columns]

In [56]:
# С помощью модуля representative_point уточняем точки внутри полигонов или линий, которыми могут быть
# обозначены остановки
stops_samara["geometry"] = stops_samara["geometry"].representative_point()
stops_samara = stops_samara[["name", "geometry"]]

stops_samara

name                   geometry
0          Храм Всех Святых  POINT (50.15169 53.19461)
1          улица Пензенская  POINT (50.13767 53.18914)
2    Железнодорожный вокзал  POINT (50.12287 53.18811)
3               парк Победы  POINT (50.20624 53.19209)
4      Автостанция «Аврора»  POINT (50.18850 53.19158)
..                      ...                        ...
307              Московская  POINT (50.16050 53.20281)
308              Российская  POINT (50.14899 53.21192)
309              Алабинская  POINT (50.13420 53.20958)
310               Юнгородок  POINT (50.28250 53.21250)
311               Кировская  POINT (50.26963 53.21135)

[312 rows x 2 columns]

In [57]:
# Переводим геометрию точек в корректную проекцию города, определённую ранее
stops_samara_crs = (
    stops_samara
    .to_crs(edges_3.crs)
)

In [58]:
# Добавляем столбец "nearest_node", куда будут добавляться ближайшие узлы графа OpenStreetMap
# к координатам, чтобы в дальнейшем по ним можно было найти кратчайший маршрут
stops_samara_crs["nearest_node"] = ""

In [59]:
# Устанавливаем столбец "name" в качестве индекса датафрейма, чтобы к датасету можно было обращаться по меткам
stops_samara_crs = stops_samara_crs.set_index("name")

In [62]:
# С помощью библиотеки osmnx ищем ближайшие узлы графа OpenStreetMap для координат
# остановочных пунктов в городе
stops_samara_crs["nearest_node"] = stops_samara_crs["geometry"].apply(
    lambda x: ox.distance.nearest_nodes(G_samara, x.x, x.y)
)

In [64]:
# Сохраняем датафрейм с остановками в Самаре в csv-файл
stops_samara_crs.to_csv("stops_samara_crs.csv")

In [71]:
# Копируем тренировочный датасет с квартирами в отдельный датафрейм, чтобы в нём собрать ближайшие узлы
# графа OpenStreetMap для координат квартир в городах
df_train_nodes = df_train.copy()

In [72]:
# Для этого добавляем столбец "geometry_crs"
df_train_nodes["geometry_crs"] = ""

df_train_nodes

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry geometry_crs  
0            True  2473000  POINT (50.16690 53.21170)               
1            True  3733000  POINT (39.09850 45.03890)               
2            True  3445000  POINT (38.97160 45.06940)               
3            True  4458000  POINT (50.26050 53.21640)               
4            True  1295000  POINT (50.38420 53.16510)               
...           ...      ...                        ...          ...  
8037         True  4029000  POINT (50.27850 53.23990)               
8038         True  5263000  POINT (38.96660 45.07390)               
8039        False  2017000  POINT (39.02880 45.11270)               
8040         True  5617000  POINT (39.01790 45.05130)               
8041         True  3729000  POINT (38.95250 45.10920)               

[8042 rows x 10 columns]

In [73]:
# Переводим координаты квартир в корректные для городов проекции, определённые ранее 
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_train_nodes.index:
    flat_crs = gpd.GeoSeries(df_train_nodes.at[i, "geometry"], crs="EPSG:4326")
    if df_train_nodes.at[i, "city"] == "Краснодар":
        df_train_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_1.crs)[0]
    elif df_train_nodes.at[i, "city"] == "Нижний Новгород":
        df_train_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_2.crs)[0]
    elif df_train_nodes.at[i, "city"] == "Самара":
        df_train_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_3.crs)[0]
        
    count_ += 1
    print(count_)

1 - 0    POINT (50.16690 53.21170)
dtype: geometry
1
1 - 0    POINT (39.09850 45.03890)
dtype: geometry
2 - POINT (507758.0518276638 4987276.430569851)
2
1 - 0    POINT (38.97160 45.06940)
dtype: geometry
2 - POINT (497764.34935612 4990660.299869019)
3
1 - 0    POINT (50.26050 53.21640)
dtype: geometry
4
1 - 0    POINT (50.38420 53.16510)
dtype: geometry
5
1 - 0    POINT (43.83690 56.24080)
dtype: geometry
6
1 - 0    POINT (39.03400 45.01870)
dtype: geometry
2 - POINT (502678.84827216703 4985028.298827317)
7
1 - 0    POINT (38.96930 45.06510)
dtype: geometry
2 - POINT (497583.1119462535 4990182.684832655)
8
1 - 0    POINT (39.01580 45.10430)
dtype: geometry
2 - POINT (501243.0203358822 4994537.035857)
9
1 - 0    POINT (38.90130 45.08900)
dtype: geometry
2 - POINT (492232.98267970263 4992841.987300971)
10
1 - 0    POINT (39.07350 45.03300)
dtype: geometry
2 - POINT (505789.5980367041 4986618.919930113)
11
1 - 0    POINT (50.17380 53.22530)
dtype: geometry
12
1 - 0    POINT (39.01640 45.

2 - POINT (501417.2853076566 4989204.805141894)
136
1 - 0    POINT (38.90570 45.09370)
dtype: geometry
2 - POINT (492579.84129593644 4993363.693109855)
137
1 - 0    POINT (38.90870 45.09290)
dtype: geometry
2 - POINT (492815.80118762306 4993274.550996012)
138
1 - 0    POINT (38.96920 45.07350)
dtype: geometry
2 - POINT (497575.59447632433 4991115.8327225335)
139
1 - 0    POINT (38.92360 45.01880)
dtype: geometry
2 - POINT (493980.48082931235 4985041.684152517)
140
1 - 0    POINT (38.91100 45.01650)
dtype: geometry
2 - POINT (492987.4521780947 4984787.196072755)
141
1 - 0    POINT (38.91150 45.01390)
dtype: geometry
2 - POINT (493026.53297001735 4984498.325093098)
142
1 - 0    POINT (43.82720 56.36180)
dtype: geometry
143
1 - 0    POINT (50.07840 53.18150)
dtype: geometry
144
1 - 0    POINT (38.90500 45.07250)
dtype: geometry
2 - POINT (492521.99541310174 4991008.67186105)
145
1 - 0    POINT (39.04700 45.01730)
dtype: geometry
2 - POINT (503703.20402644377 4984873.288200385)
146
1 - 0  

281
1 - 0    POINT (50.17630 53.18770)
dtype: geometry
282
1 - 0    POINT (38.89670 45.07750)
dtype: geometry
2 - POINT (491869.36300097645 4991564.916278303)
283
1 - 0    POINT (38.96080 45.10740)
dtype: geometry
2 - POINT (496916.2177231329 4994882.038896905)
284
1 - 0    POINT (43.98710 56.25190)
dtype: geometry
285
1 - 0    POINT (38.97710 45.01540)
dtype: geometry
2 - POINT (498195.61326401244 4984661.402386832)
286
1 - 0    POINT (38.96280 45.06250)
dtype: geometry
2 - POINT (497071.2602282896 4989894.0691959495)
287
1 - 0    POINT (43.91660 56.28470)
dtype: geometry
288
1 - 0    POINT (38.96280 45.06250)
dtype: geometry
2 - POINT (497071.2602282896 4989894.0691959495)
289
1 - 0    POINT (39.00640 45.09360)
dtype: geometry
2 - POINT (500503.595955644 4993348.279310055)
290
1 - 0    POINT (38.91620 45.01640)
dtype: geometry
2 - POINT (493397.1625816009 4984775.65029887)
291
1 - 0    POINT (43.97570 56.30300)
dtype: geometry
292
1 - 0    POINT (50.25090 53.24940)
dtype: geometry
29

2 - POINT (498332.9188195519 4997469.898996527)
450
1 - 0    POINT (39.03250 45.06490)
dtype: geometry
2 - POINT (502558.6037666537 4990160.522440246)
451
1 - 0    POINT (50.14080 53.20510)
dtype: geometry
452
1 - 0    POINT (50.24100 53.21340)
dtype: geometry
453
1 - 0    POINT (44.03640 56.30260)
dtype: geometry
454
1 - 0    POINT (38.95770 45.06760)
dtype: geometry
2 - POINT (496670.03555083275 4990460.81822068)
455
1 - 0    POINT (39.00610 45.01970)
dtype: geometry
2 - POINT (500480.6085301349 4985138.842410611)
456
1 - 0    POINT (50.17470 53.10200)
dtype: geometry
457
1 - 0    POINT (38.95390 45.07450)
dtype: geometry
2 - POINT (496371.3264451563 4991227.493710302)
458
1 - 0    POINT (50.13210 53.21300)
dtype: geometry
459
1 - 0    POINT (50.19570 53.23990)
dtype: geometry
460
1 - 0    POINT (50.18180 53.19380)
dtype: geometry
461
1 - 0    POINT (43.82120 56.23350)
dtype: geometry
462
1 - 0    POINT (50.07530 53.14810)
dtype: geometry
463
1 - 0    POINT (39.00800 45.10070)
dtype:

2 - POINT (498149.87137837213 4989949.209032457)
759
1 - 0    POINT (38.90570 45.09370)
dtype: geometry
2 - POINT (492579.84129593644 4993363.693109855)
760
1 - 0    POINT (39.03330 45.09060)
dtype: geometry
2 - POINT (502620.409888261 4993015.531319269)
761
1 - 0    POINT (43.99740 56.30020)
dtype: geometry
762
1 - 0    POINT (50.19060 53.22510)
dtype: geometry
763
1 - 0    POINT (39.00420 45.09920)
dtype: geometry
2 - POINT (500330.452546003 4993970.367532432)
764
1 - 0    POINT (50.18090 53.24200)
dtype: geometry
765
1 - 0    POINT (38.90490 45.09280)
dtype: geometry
2 - POINT (492516.7743775888 4993263.786569202)
766
1 - 0    POINT (39.02770 45.06750)
dtype: geometry
2 - POINT (502180.6188197162 4990449.21231281)
767
1 - 0    POINT (39.12310 45.04700)
dtype: geometry
2 - POINT (509694.22769544245 4988178.895935343)
768
1 - 0    POINT (38.99710 45.14050)
dtype: geometry
2 - POINT (499771.99493215105 4998558.366246502)
769
1 - 0    POINT (50.15990 53.20700)
dtype: geometry
770
1 - 0 

...

2 - POINT (503258.92092883284 4990838.483091045)
6806
1 - 0    POINT (39.03220 45.09300)
dtype: geometry
2 - POINT (502533.743682237 4993282.110161311)
6807
1 - 0    POINT (50.23900 53.24320)
dtype: geometry
6808
1 - 0    POINT (39.03220 45.09440)
dtype: geometry
2 - POINT (502533.6817770471 4993437.634978406)
6809
1 - 0    POINT (39.00570 45.06550)
dtype: geometry
2 - POINT (500448.7350434582 4990226.677699857)
6810
1 - 0    POINT (39.03770 45.09290)
dtype: geometry
2 - POINT (502966.5311651253 4993271.188221987)
6811
1 - 0    POINT (38.99950 45.09290)
dtype: geometry
2 - POINT (499960.6560853393 4993270.497108605)
6812
1 - 0    POINT (38.95370 45.10520)
dtype: geometry
2 - POINT (496357.5356171113 4994637.9374488555)
6813
1 - 0    POINT (50.16000 53.21910)
dtype: geometry
6814
1 - 0    POINT (50.18180 53.19420)
dtype: geometry
6815
1 - 0    POINT (38.94560 45.02250)
dtype: geometry
2 - POINT (495714.12627333746 4985451.309243438)
6816
1 - 0    POINT (39.10650 45.00640)
dtype: geometr

1 - 0    POINT (38.90410 45.09400)
dtype: geometry
2 - POINT (492453.9820349707 4993397.16786132)
7134
1 - 0    POINT (39.06540 44.99810)
dtype: geometry
2 - POINT (505154.69073735864 4982741.414512963)
7135
1 - 0    POINT (39.04700 45.01730)
dtype: geometry
2 - POINT (503703.20402644377 4984873.288200385)
7136
1 - 0    POINT (39.04700 45.01730)
dtype: geometry
2 - POINT (503703.20402644377 4984873.288200385)
7137
1 - 0    POINT (39.05930 45.09800)
dtype: geometry
2 - POINT (504665.7729588204 4993838.762073635)
7138
1 - 0    POINT (39.01600 45.05580)
dtype: geometry
2 - POINT (501259.8201409281 4989149.227860701)
7139
1 - 0    POINT (38.96180 45.06200)
dtype: geometry
2 - POINT (496992.5044503521 4989838.561595924)
7140
1 - 0    POINT (50.20100 53.21790)
dtype: geometry
7141
1 - 0    POINT (43.82690 56.34020)
dtype: geometry
7142
1 - 0    POINT (38.95400 45.01580)
dtype: geometry
2 - POINT (496375.49292429426 4984706.611498359)
7143
1 - 0    POINT (50.09560 53.12030)
dtype: geometry
71

2 - POINT (505492.48006746283 4984052.528399463)
7328
1 - 0    POINT (38.97210 45.09730)
dtype: geometry
2 - POINT (497804.77814384433 4993759.667964213)
7329
1 - 0    POINT (38.90000 45.08940)
dtype: geometry
2 - POINT (492130.7364647569 4992886.548555248)
7330
1 - 0    POINT (43.91880 56.16150)
dtype: geometry
7331
1 - 0    POINT (38.96460 45.06090)
dtype: geometry
2 - POINT (497212.89570706233 4989716.263992565)
7332
1 - 0    POINT (39.01500 45.10600)
dtype: geometry
2 - POINT (501180.04757296335 4994725.875817404)
7333
1 - 0    POINT (38.90100 45.08940)
dtype: geometry
2 - POINT (492209.4290999957 4992886.451772809)
7334
1 - 0    POINT (43.99590 56.33060)
dtype: geometry
7335
1 - 0    POINT (38.93990 45.03010)
dtype: geometry
2 - POINT (495265.6814384306 4986295.894228428)
7336
1 - 0    POINT (39.00280 45.09940)
dtype: geometry
2 - POINT (500220.3009282519 4993992.580619168)
7337
1 - 0    POINT (38.90100 45.08940)
dtype: geometry
2 - POINT (492209.4290999957 4992886.451772809)
7338

2 - POINT (500810.21727480803 4995370.136808093)
7528
1 - 0    POINT (39.01150 45.09100)
dtype: geometry
2 - POINT (500904.9400413415 4993059.491976202)
7529
1 - 0    POINT (38.94320 45.01870)
dtype: geometry
2 - POINT (495524.7475918966 4985029.305675668)
7530
1 - 0    POINT (38.98140 45.06910)
dtype: geometry
2 - POINT (498535.79860909167 4990626.749255814)
7531
1 - 0    POINT (38.98350 45.06530)
dtype: geometry
2 - POINT (498701.0256079668 4990204.576585206)
7532
1 - 0    POINT (38.91920 45.12240)
dtype: geometry
2 - POINT (493645.2974281646 4996550.810256244)
7533
1 - 0    POINT (50.27970 53.23810)
dtype: geometry
7534
1 - 0    POINT (50.07380 53.14480)
dtype: geometry
7535
1 - 0    POINT (39.01490 45.10580)
dtype: geometry
2 - POINT (501172.18468224443 4994703.656484556)
7536
1 - 0    POINT (39.05190 45.02800)
dtype: geometry
2 - POINT (504088.5211011628 4986062.162996466)
7537
1 - 0    POINT (38.96610 45.00510)
dtype: geometry
2 - POINT (497328.398490236 4983517.504747294)
7538
1

2 - POINT (504088.5211011628 4986062.162996466)
7797
1 - 0    POINT (50.18300 53.24270)
dtype: geometry
7798
1 - 0    POINT (38.90410 45.09280)
dtype: geometry
2 - POINT (492453.8240044114 4993263.860882534)
7799
1 - 0    POINT (39.01780 45.05240)
dtype: geometry
2 - POINT (501401.63295677915 4988771.556952699)
7800
1 - 0    POINT (43.95930 56.33040)
dtype: geometry
7801
1 - 0    POINT (39.01070 45.06220)
dtype: geometry
2 - POINT (500842.4107378512 4989860.125292508)
7802
1 - 0    POINT (39.00750 45.10070)
dtype: geometry
2 - POINT (500590.0783816186 4994137.0202259235)
7803
1 - 0    POINT (38.96100 45.02030)
dtype: geometry
2 - POINT (496927.28903019044 4985206.216671822)
7804
1 - 0    POINT (39.03770 45.09170)
dtype: geometry
2 - POINT (502966.59328850603 4993137.881268737)
7805
1 - 0    POINT (38.94570 45.06140)
dtype: geometry
2 - POINT (495724.9027109935 4989772.632765722)
7806
1 - 0    POINT (38.92420 45.01850)
dtype: geometry
2 - POINT (494027.7233540578 4985008.313432851)
7807

In [74]:
df_train_nodes

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs  
0      POINT (444364.7583481302 5896144.765920336)  
1      POINT (507758.0518276638 4987276.430569851)  
2        POINT (497764.34935612 4990660.299869019)  
3      POINT (450620.75961276994 5896598.90707207)  
4      POINT (458831.4735939478 5890813.869220274)  
...                                            ...  
8037   POINT (451849.04119317944 5899200.85693531)  
8038  POINT (497370.9552071012 4991160.3494087905)  
8039    POINT (502265.426288711 4995470.469169812)  
8040  POINT (501409.53431823035 4988649.361517621)  
8041  POINT (496263.39146830165 4995082.349866582)  

[8042 rows x 10 columns]

In [78]:
df_train_nodes["nearest_node"] = ""

df_train_nodes

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs nearest_node  
0      POINT (444364.7583481302 5896144.765920336)               
1      POINT (507758.0518276638 4987276.430569851)               
2        POINT (497764.34935612 4990660.299869019)               
3      POINT (450620.75961276994 5896598.90707207)               
4      POINT (458831.4735939478 5890813.869220274)               
...                                            ...          ...  
8037   POINT (451849.04119317944 5899200.85693531)               
8038  POINT (497370.9552071012 4991160.3494087905)               
8039    POINT (502265.426288711 4995470.469169812)               
8040  POINT (501409.53431823035 4988649.361517621)               
8041  POINT (496263.39146830165 4995082.349866582)               

[8042 rows x 11 columns]

In [79]:
# С помощью библиотеки osmnx ищем ближайшие узлы графа OpenStreetMap для координат
# квартир в каждом городе
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_train_nodes.index:
    if df_train_nodes.at[i, "city"] == "Краснодар":
        df_train_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_krasnodar, df_train_nodes.at[i, "geometry_crs"].x, df_train_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_train_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_train_nodes.at[i, "nearest_node"]}')
    elif df_train_nodes.at[i, "city"] == "Нижний Новгород":
        df_train_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_nizhny_novgorod, df_train_nodes.at[i, "geometry_crs"].x, df_train_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_train_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_train_nodes.at[i, "nearest_node"]}')
    elif df_train_nodes.at[i, "city"] == "Самара":
        df_train_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_samara, df_train_nodes.at[i, "geometry_crs"].x, df_train_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_train_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_train_nodes.at[i, "nearest_node"]}')
        
    count_ += 1
    print(count_)

1 - POINT (444364.7583481302 5896144.765920336)
2 - 1376917912
1
1 - POINT (507758.0518276638 4987276.430569851)
2 - 533897701
2
1 - POINT (497764.34935612 4990660.299869019)
2 - 921918400
3
1 - POINT (450620.75961276994 5896598.90707207)
2 - 10828204246
4
1 - POINT (458831.4735939478 5890813.869220274)
2 - 597712746
5
1 - POINT (427913.5667318893 6233488.835060305)
2 - 1827639570
6
1 - POINT (502678.84827216703 4985028.298827317)
2 - 506377215
7
1 - POINT (497583.1119462535 4990182.684832655)
2 - 11465522978
8
1 - POINT (501243.0203358822 4994537.035857)
2 - 1960834382
9
1 - POINT (492232.98267970263 4992841.987300971)
2 - 11400836784
10
1 - POINT (505789.5980367041 4986618.919930113)
2 - 11697618037
11
1 - POINT (444843.0122147199 5897652.321490302)
2 - 8863473279
12
1 - POINT (501290.7033358725 4992170.846270552)
2 - 11524545771
13
1 - POINT (498677.35485772043 4989949.077714747)
2 - 11503336426
14
1 - POINT (491861.7192294392 4991742.668497547)
2 - 11429176557
15
1 - POINT (495209.

1 - POINT (497575.6071604944 4991149.159351556)
2 - 11462814571
126
1 - POINT (497000.3513300169 4989783.013619646)
2 - 8743606359
127
1 - POINT (508615.4463413068 4988099.585041001)
2 - 11652905188
128
1 - POINT (508615.4463413068 4988099.585041001)
2 - 11652905188
129
1 - POINT (508779.0196679757 4989410.653114989)
2 - 2524789223
130
1 - POINT (508779.0196679757 4989410.653114989)
2 - 2524789223
131
1 - POINT (433706.30107409414 6237658.598650364)
2 - 1856008898
132
1 - POINT (502527.56701871514 4989016.298406709)
2 - 8158162943
133
1 - POINT (501433.447468981 4987360.743507856)
2 - 11519162072
134
1 - POINT (501433.447468981 4987360.743507856)
2 - 11519162072
135
1 - POINT (501417.2853076566 4989204.805141894)
2 - 1490222565
136
1 - POINT (492579.84129593644 4993363.693109855)
2 - 11403404215
137
1 - POINT (492815.80118762306 4993274.550996012)
2 - 11417691133
138
1 - POINT (497575.59447632433 4991115.8327225335)
2 - 11462814583
139
1 - POINT (493980.48082931235 4985041.684152517)
2

1 - POINT (449510.9211874141 5896477.002472679)
2 - 6105146739
249
1 - POINT (514900.54426652554 4991177.234774579)
2 - 8381772228
250
1 - POINT (430928.6366561775 6236311.140332784)
2 - 3118008229
251
1 - POINT (500259.81435407244 4989726.768673647)
2 - 1813636689
252
1 - POINT (496538.4485551027 4994582.291752864)
2 - 11394250906
253
1 - POINT (452960.87183755526 5896208.150336381)
2 - 6591392109
254
1 - POINT (426546.20121413586 6246570.7472947445)
2 - 1446429313
255
1 - POINT (448780.4892799504 5899355.184148412)
2 - 961876803
256
1 - POINT (496475.5174093927 4994593.435239766)
2 - 11394259623
257
1 - POINT (440915.7492618256 6236851.321676833)
2 - 8164835400
258
1 - POINT (505789.5980367041 4986618.919930113)
2 - 11697618037
259
1 - POINT (498126.5957316726 4991115.646841941)
2 - 683267323
260
1 - POINT (501417.2853076566 4989204.805141894)
2 - 1490222565
261
1 - POINT (431200.99853611225 6242051.035275516)
2 - 1439547413
262
1 - POINT (441632.88466048165 5893941.065415858)
2 - 39

1 - POINT (509219.5127725534 4984256.780823944)
2 - 2395961053
372
1 - POINT (505789.5980367041 4986618.919930113)
2 - 11697618037
373
1 - POINT (437097.2752631504 6236638.752514733)
2 - 3340145233
374
1 - POINT (447520.42989738175 5896442.82762696)
2 - 10799700467
375
1 - POINT (500503.58189360145 4993526.021980087)
2 - 11602545588
376
1 - POINT (502832.80140349927 4993182.255982727)
2 - 11531097781
377
1 - POINT (443748.1738978487 6237469.797141482)
2 - 605042081
378
1 - POINT (495331.13340432313 4989617.385094543)
2 - 2725501554
379
1 - POINT (497528.38734944095 4991171.395255564)
2 - 11462814682
380
1 - POINT (503924.9394751932 4995837.872318733)
2 - 11591713575
381
1 - POINT (501314.03171023366 4993537.246614281)
2 - 4716054303
382
1 - POINT (509791.5765056646 4986323.869388738)
2 - 1778850190
383
1 - POINT (500440.64723019575 4993337.165725943)
2 - 5253792252
384
1 - POINT (449972.91051950364 5899776.433303584)
2 - 962284850
385
1 - POINT (505620.1561974233 4982241.914166452)
2 -

1 - POINT (500527.4641680967 4990182.248290398)
2 - 344601788
494
1 - POINT (447917.0707753416 5899742.801509032)
2 - 2468444980
495
1 - POINT (442743.6744301563 6238295.777895965)
2 - 2503131309
496
1 - POINT (502691.83282175235 4991593.622055151)
2 - 11880572140
497
1 - POINT (507422.7218431387 4984398.8527380135)
2 - 9004386270
498
1 - POINT (507422.7218431387 4984398.8527380135)
2 - 9004386270
499
1 - POINT (507422.7218431387 4984398.8527380135)
2 - 9004386270
500
1 - POINT (500904.9400413415 4993059.491976202)
2 - 11618852693
501
1 - POINT (500110.15065639745 4993981.468832924)
2 - 11598296452
502
1 - POINT (448695.91227229586 5911316.257002888)
2 - 494157969
503
1 - POINT (499078.5349749302 4987616.151669096)
2 - 2487592859
504
1 - POINT (499495.97270770307 4987893.825438049)
2 - 11510985259
505
1 - POINT (439059.6392940793 6241753.209936538)
2 - 1636762020
506
1 - POINT (505784.3785654193 4983686.197200124)
2 - 562950965
507
1 - POINT (429287.7704494612 6234490.0399128245)
2 - 1

...

1 - POINT (496782.5215925653 4994959.867722876)
2 - 11385839267
7481
1 - POINT (495603.53724699555 4985029.250913353)
2 - 295170395
7482
1 - POINT (502361.5245508619 4990871.413840987)
2 - 3981311278
7483
1 - POINT (492461.33761524246 4992963.910959875)
2 - 7578704050
7484
1 - POINT (497668.6788416404 4987361.008526395)
2 - 9119926151
7485
1 - POINT (492521.99541310174 4991008.67186105)
2 - 7991150450
7486
1 - POINT (501290.6988325188 4992193.064060157)
2 - 11524545771
7487
1 - POINT (492579.84129593644 4993363.693109855)
2 - 11403404215
7488
1 - POINT (503497.3715621474 4986650.577728879)
2 - 11665466618
7489
1 - POINT (500094.4171555647 4993825.943628882)
2 - 11602545859
7490
1 - POINT (495931.9670178826 4993471.757411993)
2 - 9069341747
7491
1 - POINT (494627.43171892606 4995416.789752819)
2 - 11443469337
7492
1 - POINT (497136.5578831895 4995037.461158717)
2 - 11181841703
7493
1 - POINT (511857.9950713464 4989193.460349688)
2 - 567077710
7494
1 - POINT (492674.4443617161 4993519.10

1 - POINT (508788.7309146092 4988077.603856271)
2 - 11652905160
7601
1 - POINT (438432.80495656806 6239903.187174619)
2 - 10944181763
7602
1 - POINT (452609.32881123084 5907860.055345392)
2 - 1131315950
7603
1 - POINT (444843.0122147199 5897652.321490302)
2 - 8863473279
7604
1 - POINT (503604.1730122165 4992793.834041474)
2 - 4210190648
7605
1 - POINT (447013.6329062759 5900720.684885926)
2 - 2425133290
7606
1 - POINT (437761.7051668969 6240992.739722549)
2 - 1232969510
7607
1 - POINT (440066.9525134906 6238154.454186337)
2 - 2096186932
7608
1 - POINT (501211.51127777237 4994748.099610798)
2 - 11594478067
7609
1 - POINT (495822.2961087729 4994216.126676227)
2 - 5199376738
7610
1 - POINT (446516.35004580667 5893249.779913722)
2 - 12017211221
7611
1 - POINT (439711.6223149658 6241922.040890655)
2 - 6518725708
7612
1 - POINT (436775.8364799618 6241274.427512622)
2 - 1622779400
7613
1 - POINT (497202.37334763183 4983673.081164117)
2 - 4759496369
7614
1 - POINT (505225.63593767874 4982730.3

1 - POINT (439678.9567554471 6229966.931113891)
2 - 2920803671
7721
1 - POINT (492592.8009152726 4990975.262468761)
2 - 7991150451
7722
1 - POINT (495591.01377204206 4989706.070849148)
2 - 7369200899
7723
1 - POINT (502092.24134317023 4995870.332315379)
2 - 4840250153
7724
1 - POINT (493822.9232972621 4985064.052263414)
2 - 9921507570
7725
1 - POINT (500251.8168727129 4992870.581191675)
2 - 5102850603
7726
1 - POINT (447289.8166146191 5897936.203669257)
2 - 947039126
7727
1 - POINT (492624.5703913555 4991219.621198786)
2 - 9158462925
7728
1 - POINT (497504.22497112857 4989771.687507572)
2 - 11465890480
7729
1 - POINT (497202.70435676957 4984428.476287349)
2 - 11505938609
7730
1 - POINT (496711.7213342374 4994959.9039213825)
2 - 11387519056
7731
1 - POINT (495603.5219419872 4985007.033375733)
2 - 295170395
7732
1 - POINT (502715.82900482445 4990693.813079282)
2 - 11521562057
7733
1 - POINT (504088.5211011628 4986062.162996466)
2 - 11669259897
7734
1 - POINT (503608.6729791651 4984839.90

1 - POINT (497668.6788416404 4987361.008526395)
2 - 9119926151
7842
1 - POINT (453673.1663426618 5908327.98136625)
2 - 1305235117
7843
1 - POINT (500740.15465253027 4989060.275604475)
2 - 2157343454
7844
1 - POINT (495591.075257597 4989794.941665301)
2 - 8130092940
7845
1 - POINT (500440.64646118926 4993348.27464116)
2 - 6682956768
7846
1 - POINT (442247.54347618914 5893933.600862039)
2 - 6822502172
7847
1 - POINT (502112.1176675116 4983350.664033321)
2 - 11693632116
7848
1 - POINT (500779.91031898296 4985905.377641103)
2 - 2984571401
7849
1 - POINT (434014.3367809099 6238355.147973435)
2 - 4609562255
7850
1 - POINT (435884.75217853894 6233027.769016458)
2 - 4134267594
7851
1 - POINT (503290.0752776091 4991482.814132598)
2 - 11554269336
7852
1 - POINT (497425.4714582085 4989716.174568504)
2 - 11465890472
7853
1 - POINT (498424.96410585276 4988093.958835802)
2 - 4746736822
7854
1 - POINT (430280.3596881795 6235687.140097419)
2 - 1836368701
7855
1 - POINT (448542.20605270844 5911262.2891

1 - POINT (501588.9975488388 4995259.194160388)
2 - 3755647580
7963
1 - POINT (505288.60757790034 4982830.393898242)
2 - 5618517605
7964
1 - POINT (497660.7701599159 4987272.140936483)
2 - 9134874024
7965
1 - POINT (501172.18468224443 4994703.656484556)
2 - 11594478092
7966
1 - POINT (501172.1805891434 4994725.874363239)
2 - 11594478092
7967
1 - POINT (507765.75216925616 4987420.8546822425)
2 - 530173000
7968
1 - POINT (502580.87522166566 4993482.089614856)
2 - 8595826489
7969
1 - POINT (493767.67319557955 4984964.126964379)
2 - 2279192837
7970
1 - POINT (435718.74493579223 6233119.319997486)
2 - 613546788
7971
1 - POINT (437074.50745581964 6235514.760177282)
2 - 4908434464
7972
1 - POINT (507430.58865912573 4984409.970663581)
2 - 9004386270
7973
1 - POINT (495739.0602842889 4987395.332278674)
2 - 420375462
7974
1 - POINT (494462.8038714098 4996061.250933012)
2 - 1772524030
7975
1 - POINT (492516.7743775888 4993263.786569202)
2 - 8037355817
7976
1 - POINT (442201.1370040114 5893411.249

In [80]:
df_train_nodes

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs nearest_node  
0      POINT (444364.7583481302 5896144.765920336)   1376917912  
1      POINT (507758.0518276638 4987276.430569851)    533897701  
2        POINT (497764.34935612 4990660.299869019)    921918400  
3      POINT (450620.75961276994 5896598.90707207)  10828204246  
4      POINT (458831.4735939478 5890813.869220274)    597712746  
...                                            ...          ...  
8037   POINT (451849.04119317944 5899200.85693531)   1567984170  
8038  POINT (497370.9552071012 4991160.3494087905)  11462814570  
8039    POINT (502265.426288711 4995470.469169812)   7310019142  
8040  POINT (501409.53431823035 4988649.361517621)    295196089  
8041  POINT (496263.39146830165 4995082.349866582)  11394107436  

[8042 rows x 11 columns]

In [82]:
# Сохраняем датафрейм с узлами графа OpenStreetMap в csv-файл
df_train_nodes.to_csv("df_train_nodes.csv")

In [83]:
# Копируем полученный датасет с узлами графа OpenStreetMap, чтобы по этим узлам найти количество
# ближайших остановок, находящихся в пешей доступности от квартиры
df_train_nodes_copy = df_train_nodes.copy()

In [84]:
df_train_nodes_copy["count_stops"] = ""
df_train_nodes_copy

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs nearest_node count_stops  
0      POINT (444364.7583481302 5896144.765920336)   1376917912              
1      POINT (507758.0518276638 4987276.430569851)    533897701              
2        POINT (497764.34935612 4990660.299869019)    921918400              
3      POINT (450620.75961276994 5896598.90707207)  10828204246              
4      POINT (458831.4735939478 5890813.869220274)    597712746              
...                                            ...          ...         ...  
8037   POINT (451849.04119317944 5899200.85693531)   1567984170              
8038  POINT (497370.9552071012 4991160.3494087905)  11462814570              
8039    POINT (502265.426288711 4995470.469169812)   7310019142              
8040  POINT (501409.53431823035 4988649.361517621)    295196089              
8041  POINT (496263.39146830165 4995082.349866582)  11394107436              

[8042 rows x 12 columns]

In [85]:
# С помощью библиотеки networkx находим остановки, находящиеся от квартиры на расстоянии не более,
# чем в 1 км (1000 м).
# Для этого пройдёмся по датасетам (с остановками в городах и с квартирами)
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_train_nodes_copy.index:
    if df_train_nodes_copy.at[i, "count_stops"] == "":
        if df_train_nodes_copy.at[i, "city"] == "Краснодар":
            count_stop = 0 # задаём счётчик для увеличения количества найденных остановок на указанном расстоянии
            for j in stops_krasnodar_crs.index:
                try:
                    '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_krasnodar, df_train_nodes_copy.at[i, "nearest_node"], stops_krasnodar_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_train_nodes_copy.at[i, "count_stops"] = count_stop
            print(count_)

        elif df_train_nodes_copy.at[i, "city"] == "Нижний Новгород":
            count_stop = 0 # задаём счётчик для увеличения количества найденных остановок на указанном расстоянии
            for j in stops_nizhny_crs.index:
                try:
                    '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_nizhny_novgorod, df_train_nodes_copy.at[i, "nearest_node"], stops_nizhny_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_train_nodes_copy.at[i, "count_stops"] = count_stop
            print(count_)

        elif df_train_nodes_copy.at[i, "city"] == "Самара":
            count_stop = 0 # задаём счётчик для увеличения количества найденных остановок на указанном расстоянии
            for j in stops_samara_crs.index:
                try:
                    '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_samara, df_train_nodes_copy.at[i, "nearest_node"], stops_samara_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_train_nodes_copy.at[i, "count_stops"] = count_stop
        count_ += 1
        print(f'Проработано: {count_} объектов')
    else:
        continue


Проработано: 1 объектов
1
Проработано: 2 объектов
2
Проработано: 3 объектов
Проработано: 4 объектов
Проработано: 5 объектов
5
Проработано: 6 объектов
6
Проработано: 7 объектов
7
Проработано: 8 объектов
8
Проработано: 9 объектов
9
Проработано: 10 объектов
10
Проработано: 11 объектов
Проработано: 12 объектов
12
Проработано: 13 объектов
13
Проработано: 14 объектов
14
Проработано: 15 объектов
15
Проработано: 16 объектов
16
Проработано: 17 объектов
17
Проработано: 18 объектов
Проработано: 19 объектов
Проработано: 20 объектов
20
Проработано: 21 объектов
Проработано: 22 объектов
22
Проработано: 23 объектов
23
Проработано: 24 объектов
Проработано: 25 объектов
Проработано: 26 объектов
Проработано: 27 объектов
27
Проработано: 28 объектов
Проработано: 29 объектов
Проработано: 30 объектов
30
Проработано: 31 объектов
31
Проработано: 32 объектов
32
Проработано: 33 объектов
33
Проработано: 34 объектов
34
Проработано: 35 объектов
Проработано: 36 объектов
36
Проработано: 37 объектов
37
Проработано: 38 

290
Проработано: 291 объектов
291
Проработано: 292 объектов
Проработано: 293 объектов
293
Проработано: 294 объектов
Проработано: 295 объектов
295
Проработано: 296 объектов
Проработано: 297 объектов
297
Проработано: 298 объектов
Проработано: 299 объектов
299
Проработано: 300 объектов
Проработано: 301 объектов
301
Проработано: 302 объектов
302
Проработано: 303 объектов
303
Проработано: 304 объектов
304
Проработано: 305 объектов
305
Проработано: 306 объектов
306
Проработано: 307 объектов
307
Проработано: 308 объектов
Проработано: 309 объектов
Проработано: 310 объектов
Проработано: 311 объектов
Проработано: 312 объектов
312
Проработано: 313 объектов
313
Проработано: 314 объектов
Проработано: 315 объектов
Проработано: 316 объектов
316
Проработано: 317 объектов
317
Проработано: 318 объектов
318
Проработано: 319 объектов
Проработано: 320 объектов
320
Проработано: 321 объектов
321
Проработано: 322 объектов
Проработано: 323 объектов
323
Проработано: 324 объектов
324
Проработано: 325 объектов
32

570
Проработано: 571 объектов
571
Проработано: 572 объектов
Проработано: 573 объектов
573
Проработано: 574 объектов
574
Проработано: 575 объектов
Проработано: 576 объектов
576
Проработано: 577 объектов
577
Проработано: 578 объектов
578
Проработано: 579 объектов
579
Проработано: 580 объектов
Проработано: 581 объектов
581
Проработано: 582 объектов
582
Проработано: 583 объектов
583
Проработано: 584 объектов
584
Проработано: 585 объектов
585
Проработано: 586 объектов
586
Проработано: 587 объектов
587
Проработано: 588 объектов
588
Проработано: 589 объектов
589
Проработано: 590 объектов
590
Проработано: 591 объектов
591
Проработано: 592 объектов
Проработано: 593 объектов
593
Проработано: 594 объектов
594
Проработано: 595 объектов
Проработано: 596 объектов
596
Проработано: 597 объектов
597
Проработано: 598 объектов
598
Проработано: 599 объектов
599
Проработано: 600 объектов
Проработано: 601 объектов
Проработано: 602 объектов
602
Проработано: 603 объектов
603
Проработано: 604 объектов
604
Прор

851
Проработано: 852 объектов
Проработано: 853 объектов
Проработано: 854 объектов
Проработано: 855 объектов
Проработано: 856 объектов
Проработано: 857 объектов
857
Проработано: 858 объектов
858
Проработано: 859 объектов
859
Проработано: 860 объектов
860
Проработано: 861 объектов
Проработано: 862 объектов
Проработано: 863 объектов
863
Проработано: 864 объектов
864
Проработано: 865 объектов
865
Проработано: 866 объектов
866
Проработано: 867 объектов
Проработано: 868 объектов
868
Проработано: 869 объектов
869
Проработано: 870 объектов
Проработано: 871 объектов
Проработано: 872 объектов
872
Проработано: 873 объектов
873
Проработано: 874 объектов
874
Проработано: 875 объектов
875
Проработано: 876 объектов
876
Проработано: 877 объектов
Проработано: 878 объектов
878
Проработано: 879 объектов
879
Проработано: 880 объектов
880
Проработано: 881 объектов
881
Проработано: 882 объектов
882
Проработано: 883 объектов
883
Проработано: 884 объектов
Проработано: 885 объектов
885
Проработано: 886 объекто

Проработано: 1126 объектов
Проработано: 1127 объектов
Проработано: 1128 объектов
1128
Проработано: 1129 объектов
1129
Проработано: 1130 объектов
1130
Проработано: 1131 объектов
1131
Проработано: 1132 объектов
1132
Проработано: 1133 объектов
Проработано: 1134 объектов
1134
Проработано: 1135 объектов
Проработано: 1136 объектов
1136
Проработано: 1137 объектов
1137
Проработано: 1138 объектов
1138
Проработано: 1139 объектов
1139
Проработано: 1140 объектов
1140
Проработано: 1141 объектов
1141
Проработано: 1142 объектов
Проработано: 1143 объектов
1143
Проработано: 1144 объектов
1144
Проработано: 1145 объектов
1145
Проработано: 1146 объектов
Проработано: 1147 объектов
1147
Проработано: 1148 объектов
1148
Проработано: 1149 объектов
1149
Проработано: 1150 объектов
Проработано: 1151 объектов
Проработано: 1152 объектов
1152
Проработано: 1153 объектов
1153
Проработано: 1154 объектов
1154
Проработано: 1155 объектов
1155
Проработано: 1156 объектов
1156
Проработано: 1157 объектов
1157
Проработано: 115

...

6922
Проработано: 6923 объектов
6923
Проработано: 6924 объектов
6924
Проработано: 6925 объектов
6925
Проработано: 6926 объектов
6926
Проработано: 6927 объектов
6927
Проработано: 6928 объектов
6928
Проработано: 6929 объектов
Проработано: 6930 объектов
6930
Проработано: 6931 объектов
6931
Проработано: 6932 объектов
6932
Проработано: 6933 объектов
6933
Проработано: 6934 объектов
6934
Проработано: 6935 объектов
6935
Проработано: 6936 объектов
6936
Проработано: 6937 объектов
Проработано: 6938 объектов
6938
Проработано: 6939 объектов
6939
Проработано: 6940 объектов
6940
Проработано: 6941 объектов
6941
Проработано: 6942 объектов
6942
Проработано: 6943 объектов
6943
Проработано: 6944 объектов
6944
Проработано: 6945 объектов
6945
Проработано: 6946 объектов
6946
Проработано: 6947 объектов
6947
Проработано: 6948 объектов
6948
Проработано: 6949 объектов
6949
Проработано: 6950 объектов
6950
Проработано: 6951 объектов
6951
Проработано: 6952 объектов
6952
Проработано: 6953 объектов
6953
Проработано: 

Проработано: 7186 объектов
7186
Проработано: 7187 объектов
7187
Проработано: 7188 объектов
7188
Проработано: 7189 объектов
7189
Проработано: 7190 объектов
7190
Проработано: 7191 объектов
7191
Проработано: 7192 объектов
7192
Проработано: 7193 объектов
7193
Проработано: 7194 объектов
7194
Проработано: 7195 объектов
7195
Проработано: 7196 объектов
Проработано: 7197 объектов
7197
Проработано: 7198 объектов
Проработано: 7199 объектов
7199
Проработано: 7200 объектов
Проработано: 7201 объектов
7201
Проработано: 7202 объектов
7202
Проработано: 7203 объектов
7203
Проработано: 7204 объектов
7204
Проработано: 7205 объектов
7205
Проработано: 7206 объектов
7206
Проработано: 7207 объектов
7207
Проработано: 7208 объектов
7208
Проработано: 7209 объектов
7209
Проработано: 7210 объектов
7210
Проработано: 7211 объектов
7211
Проработано: 7212 объектов
7212
Проработано: 7213 объектов
7213
Проработано: 7214 объектов
7214
Проработано: 7215 объектов
7215
Проработано: 7216 объектов
7216
Проработано: 7217 объек

7448
Проработано: 7449 объектов
7449
Проработано: 7450 объектов
7450
Проработано: 7451 объектов
7451
Проработано: 7452 объектов
7452
Проработано: 7453 объектов
7453
Проработано: 7454 объектов
Проработано: 7455 объектов
7455
Проработано: 7456 объектов
7456
Проработано: 7457 объектов
7457
Проработано: 7458 объектов
7458
Проработано: 7459 объектов
7459
Проработано: 7460 объектов
7460
Проработано: 7461 объектов
Проработано: 7462 объектов
7462
Проработано: 7463 объектов
7463
Проработано: 7464 объектов
7464
Проработано: 7465 объектов
7465
Проработано: 7466 объектов
7466
Проработано: 7467 объектов
7467
Проработано: 7468 объектов
7468
Проработано: 7469 объектов
7469
Проработано: 7470 объектов
7470
Проработано: 7471 объектов
Проработано: 7472 объектов
7472
Проработано: 7473 объектов
7473
Проработано: 7474 объектов
7474
Проработано: 7475 объектов
7475
Проработано: 7476 объектов
7476
Проработано: 7477 объектов
7477
Проработано: 7478 объектов
7478
Проработано: 7479 объектов
7479
Проработано: 7480 

7711
Проработано: 7712 объектов
7712
Проработано: 7713 объектов
7713
Проработано: 7714 объектов
7714
Проработано: 7715 объектов
7715
Проработано: 7716 объектов
7716
Проработано: 7717 объектов
7717
Проработано: 7718 объектов
7718
Проработано: 7719 объектов
7719
Проработано: 7720 объектов
7720
Проработано: 7721 объектов
7721
Проработано: 7722 объектов
7722
Проработано: 7723 объектов
7723
Проработано: 7724 объектов
7724
Проработано: 7725 объектов
7725
Проработано: 7726 объектов
Проработано: 7727 объектов
7727
Проработано: 7728 объектов
7728
Проработано: 7729 объектов
7729
Проработано: 7730 объектов
7730
Проработано: 7731 объектов
7731
Проработано: 7732 объектов
7732
Проработано: 7733 объектов
7733
Проработано: 7734 объектов
7734
Проработано: 7735 объектов
7735
Проработано: 7736 объектов
7736
Проработано: 7737 объектов
7737
Проработано: 7738 объектов
7738
Проработано: 7739 объектов
Проработано: 7740 объектов
7740
Проработано: 7741 объектов
7741
Проработано: 7742 объектов
7742
Проработано: 

7974
Проработано: 7975 объектов
7975
Проработано: 7976 объектов
Проработано: 7977 объектов
Проработано: 7978 объектов
7978
Проработано: 7979 объектов
7979
Проработано: 7980 объектов
7980
Проработано: 7981 объектов
7981
Проработано: 7982 объектов
Проработано: 7983 объектов
7983
Проработано: 7984 объектов
7984
Проработано: 7985 объектов
Проработано: 7986 объектов
7986
Проработано: 7987 объектов
7987
Проработано: 7988 объектов
7988
Проработано: 7989 объектов
7989
Проработано: 7990 объектов
7990
Проработано: 7991 объектов
7991
Проработано: 7992 объектов
7992
Проработано: 7993 объектов
7993
Проработано: 7994 объектов
7994
Проработано: 7995 объектов
Проработано: 7996 объектов
7996
Проработано: 7997 объектов
7997
Проработано: 7998 объектов
7998
Проработано: 7999 объектов
7999
Проработано: 8000 объектов
8000
Проработано: 8001 объектов
8001
Проработано: 8002 объектов
8002
Проработано: 8003 объектов
8003
Проработано: 8004 объектов
8004
Проработано: 8005 объектов
8005
Проработано: 8006 объектов
8

In [96]:
# Сохраняем датафрейм с количеством найденных остановок в csv-файл
df_train_nodes_copy.to_csv("df_train_stops.csv")

In [97]:
# Выгружаем зелёные зоны (парки, сады, стадионы) города из OpenStreetMap
tags = {"leisure":["park", "garden", "stadium"]}

features_park_krasnodar = ox.features.features_from_place("Krasnodar", tags=tags)

In [98]:
features_park_krasnodar

barrier opening_hours  \
element_type osmid                              
node         7124254922     NaN           NaN   
way          26939146       NaN           NaN   
             26940686       NaN           NaN   
             26940707       NaN           NaN   
             26940896       NaN           NaN   
...                         ...           ...   
relation     11946152     fence           NaN   
             13059630       NaN           NaN   
             13221332       NaN           NaN   
             13264624       NaN           NaN   
             17247474       NaN           NaN   

                                                                  geometry  \
element_type osmid                                                           
node         7124254922                          POINT (39.06139 45.00442)   
way          26939146    POLYGON ((38.92787 45.05768, 38.93285 45.05487...   
             26940686    POLYGON ((38.97219 45.02357, 38.97259 45.02483...   
             26940707    POLYGON ((39.05436 45.01132, 39.05427 45.01125...   
             26940896    POLYGON ((38.96695 45.02127, 38.96744 45.02257...   
...                                                                    ...   
relation     11946152    POLYGON ((38.99728 45.02607, 38.99783 45.02621...   
             13059630    POLYGON ((38.96187 45.13623, 38.96301 45.13624...   
             13221332    POLYGON ((38.95141 45.01164, 38.95178 45.01002...   
             13264624    POLYGON ((38.97459 45.06987, 38.97458 45.06985...   
             17247474    POLYGON ((39.03493 45.04448, 39.03493 45.04489...   

                                                                   name  \
element_type osmid                                                        
node         7124254922                                          Лотосы   
way          26939146    Ботанический сад имени профессора И.С. Косенко   
             26940686                  Сквер имени маршала Г. К. Жукова   
             26940707                                  Солнечный остров   
             26940896                              Сквер Дружбы народов   
...                                                                 ...   
relation     11946152                                  Стадион "Кубань"   
             13059630                                         Санторини   
             13221332      Парк культуры и отдыха имени 30-летия Победы   
             13264624                                               NaN   
             17247474                                      Японский сад   

                        access  leisure name:ja  \
element_type osmid                                
node         7124254922    yes   garden     NaN   
way          26939146      NaN     park     NaN   
             26940686      NaN     park     NaN   
             26940707      NaN     park     NaN   
             26940896      NaN     park     NaN   
...                        ...      ...     ...   
relation     11946152      NaN  stadium     NaN   
             13059630      NaN     park     NaN   
             13221332      NaN     park     NaN   
             13264624      NaN  stadium     NaN   
             17247474      NaN     park    和風庭園   

                                                                     nodes  \
element_type osmid                                                           
node         7124254922                                                NaN   
way          26939146    [295188162, 295188161, 510916925, 2501132190, ...   
             26940686    [1809807393, 1809807429, 1809807431, 180980739...   
             26940707    [304774617, 295165235, 295165234, 1804793792, ...   
             26940896    [295169614, 295169613, 295169616, 295169615, 2...   
...                                                                    ...   
relation     11946152    [[[496246767, 521525962, 6900368698, 690036860...   
             13059630    [[[7

In [99]:
import folium
import matplotlib.pyplot as plt

In [105]:
type(features_park_krasnodar)

geopandas.geodataframe.GeoDataFrame

In [161]:
# Переводим координаты в геодатафрейме с зелёными зонами города в проекцию EPSG:32637 (UTM Zone 37N)
park_krasnodar_1500 = features_park_krasnodar.to_crs(32637)
# создаём буферную зону в размере 1500 м вокруг каждого геометрического объекта в наборе
park_krasnodar_1500["geometry"] = park_krasnodar_1500["geometry"].buffer(1500)
# переводим полученные координаты в EPSG:4326 (WGS84)
park_krasnodar_1500 = park_krasnodar_1500.to_crs(4326)

In [162]:
park_krasnodar_1500

barrier opening_hours  \
element_type osmid                              
node         7124254922     NaN           NaN   
way          26939146       NaN           NaN   
             26940686       NaN           NaN   
             26940707       NaN           NaN   
             26940896       NaN           NaN   
...                         ...           ...   
relation     11946152     fence           NaN   
             13059630       NaN           NaN   
             13221332       NaN           NaN   
             13264624       NaN           NaN   
             17247474       NaN           NaN   

                                                                  geometry  \
element_type osmid                                                           
node         7124254922  POLYGON ((39.08043 45.00441, 39.08033 45.00308...   
way          26939146    POLYGON ((38.91303 45.06615, 38.91427 45.06713...   
             26940686    POLYGON ((38.96758 45.01047, 38.96579 45.01079...   
             26940707    POLYGON ((39.04197 44.99280, 39.04091 44.99342...   
             26940896    POLYGON ((38.96255 45.00813, 38.96063 45.00845...   
...                                                                    ...   
relation     11946152    POLYGON ((38.97824 45.02599, 38.97832 45.02728...   
             13059630    POLYGON ((38.94279 45.13626, 38.94288 45.13757...   
             13221332    POLYGON ((38.93327 45.02587, 38.93328 45.02588...   
             13264624    POLYGON ((38.99357 45.06871, 38.99336 45.06756...   
             17247474    POLYGON ((39.01589 45.04433, 39.01588 45.04471...   

                                                                   name  \
element_type osmid                                                        
node         7124254922                                          Лотосы   
way          26939146    Ботанический сад имени профессора И.С. Косенко   
             26940686                  Сквер имени маршала Г. К. Жукова   
             26940707                                  Солнечный остров   
             26940896                              Сквер Дружбы народов   
...                                                                 ...   
relation     11946152                                  Стадион "Кубань"   
             13059630                                         Санторини   
             13221332      Парк культуры и отдыха имени 30-летия Победы   
             13264624                                               NaN   
             17247474                                      Японский сад   

                        access  leisure name:ja  \
element_type osmid                                
node         7124254922    yes   garden     NaN   
way          26939146      NaN     park     NaN   
             26940686      NaN     park     NaN   
             26940707      NaN     park     NaN   
             26940896      NaN     park     NaN   
...                        ...      ...     ...   
relation     11946152      NaN  stadium     NaN   
             13059630      NaN     park     NaN   
             13221332      NaN     park     NaN   
             13264624      NaN  stadium     NaN   
             17247474      NaN     park    和風庭園   

                                                                     nodes  \
element_type osmid                                                           
node         7124254922                                                NaN   
way          26939146    [295188162, 295188161, 510916925, 2501132190, ...   
             26940686    [1809807393, 1809807429, 1809807431, 180980739...   
             26940707    [304774617, 295165235, 295165234, 1804793792, ...   
             26940896    [295169614, 295169613, 295169616, 295169615, 2...   
...                                                                    ...   
relation     11946152    [[[496246767, 521525962, 6900368698, 690036860...   
             13059630    [[[7

In [203]:
# Для дальнейшей работы создаём новый геодатафрейм на основе полученного набора данных
gdf_park_krasnodar_1500 = park_krasnodar_1500_geom.to_frame()

In [204]:
type(gdf_park_krasnodar_1500)

geopandas.geodataframe.GeoDataFrame

In [218]:
gdf_park_krasnodar_1500

geometry
element_type osmid                                                        
node         7124254922  POLYGON ((39.08043 45.00441, 39.08033 45.00308...
way          26939146    POLYGON ((38.91303 45.06615, 38.91427 45.06713...
             26940686    POLYGON ((38.96758 45.01047, 38.96579 45.01079...
             26940707    POLYGON ((39.04197 44.99280, 39.04091 44.99342...
             26940896    POLYGON ((38.96255 45.00813, 38.96063 45.00845...
...                                                                    ...
relation     11946152    POLYGON ((38.97824 45.02599, 38.97832 45.02728...
             13059630    POLYGON ((38.94279 45.13626, 38.94288 45.13757...
             13221332    POLYGON ((38.93327 45.02587, 38.93328 45.02588...
             13264624    POLYGON ((38.99357 45.06871, 38.99336 45.06756...
             17247474    POLYGON ((39.01589 45.04433, 39.01588 45.04471...

[249 rows x 1 columns]

In [227]:
# Выгружаем зелёные зоны (парки, сады, стадионы) города из OpenStreetMap
tags = {"leisure":["park", "garden", "stadium"]}

features_park_nizhny = ox.features.features_from_place("Nizhny Novgorod", tags=tags)

In [228]:
features_park_nizhny

barrier  \
element_type osmid              
way          28501972     NaN   
             35979423     NaN   
             43052698   fence   
             48519800   fence   
             54512879   fence   
...                       ...   
relation     7819812      NaN   
             8310106      NaN   
             9802449      NaN   
             10581909     NaN   
             13108789     NaN   

                                                                geometry  \
element_type osmid                                                         
way          28501972  POLYGON ((43.99233 56.30879, 43.99556 56.30941...   
             35979423  POLYGON ((44.00594 56.31554, 44.00629 56.31562...   
             43052698  POLYGON ((43.83941 56.29144, 43.83979 56.29113...   
             48519800  POLYGON ((44.01535 56.24979, 44.01539 56.24921...   
             54512879  POLYGON ((43.84363 56.32967, 43.84575 56.32920...   
...                                                                  ...   
relation     7819812   POLYGON ((43.99588 56.31631, 43.99728 56.31662...   
             8310106   POLYGON ((43.96850 56.33396, 43.97060 56.33550...   
             9802449   POLYGON ((43.85769 56.23484, 43.85581 56.23634...   
             10581909  POLYGON ((43.97039 56.25726, 43.97045 56.25729...   
             13108789  POLYGON ((43.97059 56.33167, 43.97058 56.33168...   

                           access                     name description  \
element_type osmid                                                       
way          28501972         NaN  Парк имени А.С. Пушкина         NaN   
             35979423         NaN      Парк имени Кулибина         NaN   
             43052698         NaN                      NaN         NaN   
             48519800  permissive    Ботанический сад ННГУ         NaN   
             54512879         NaN                    Полёт         NaN   
...                           ...                      ...         ...   
relation     7819812          NaN                      NaN         NaN   
             8310106          NaN                      NaN         NaN   
             9802449          NaN                      NaN         NaN   
             10581909         NaN      Сквер Первых маёвок         NaN   
             13108789         NaN                  Стрелка         NaN   

                      tourism  \
element_type osmid              
way          28501972     NaN   
             35979423     NaN   
             43052698     NaN   
             48519800     NaN   
             54512879     NaN   
...                       ...   
relation     7819812      NaN   
             8310106      NaN   
             9802449      NaN   
             10581909     NaN   
             13108789     NaN   

                                                                   nodes  \
element_type osmid                                                         
way          28501972  [313109463, 313109464, 313109465, 420212759, 3...   
             35979423  [1627193723, 1627193731, 1290609521, 420538570...   
             43052698  [539341288, 539341286, 539341290, 539341292, 5...   
             48519800  [616409345, 616409342, 616409343, 616413472, 6...   
             54512879  [1108812771, 1108812770, 1108812774, 388459819...   
...                                                                  ...   
relation     7819812   [[[6566445147, 6566445146, 6566445148, 6566445...   
             8310106   [[[550703162, 5584608335, 5584608331, 55846083...   
             9802449   [[[6620696061, 6620696057, 6620696056, 6620696...   
             10581909  [[[1243300601, 5208854379, 7128173697, 3808121...   
             13108789  [[[259472319, 9853356711, 1711797457, 13135052...   

                             alt_name  leisure  \
element_type osmid                               
way          28501972  Пушкинский сад     park   
             35979423             NaN     park   
             43052698

In [229]:
type(features_park_nizhny)

geopandas.geodataframe.GeoDataFrame

In [231]:
# Переводим координаты в геодатафрейме с зелёными зонами города в проекцию EPSG:32637 (UTM Zone 37N)
park_nizhny_1500 = features_park_nizhny.to_crs(32637)
# создаём буферную зону в размере 1500 м вокруг каждого геометрического объекта в наборе
park_nizhny_1500["geometry"] = park_nizhny_1500["geometry"].buffer(1500)
# переводим полученные координаты в EPSG:4326 (WGS84)
park_nizhny_1500 = park_nizhny_1500.to_crs(4326)

In [232]:
park_nizhny_1500

barrier  \
element_type osmid              
way          28501972     NaN   
             35979423     NaN   
             43052698   fence   
             48519800   fence   
             54512879   fence   
...                       ...   
relation     7819812      NaN   
             8310106      NaN   
             9802449      NaN   
             10581909     NaN   
             13108789     NaN   

                                                                geometry  \
element_type osmid                                                         
way          28501972  POLYGON ((43.97108 56.30236, 43.97070 56.30274...   
             35979423  POLYGON ((43.98338 56.32120, 43.98427 56.32230...   
             43052698  POLYGON ((43.82580 56.30257, 43.82606 56.30267...   
             48519800  POLYGON ((43.99139 56.25160, 43.99147 56.25192...   
             54512879  POLYGON ((43.82099 56.33446, 43.82195 56.33568...   
...                                                                  ...   
relation     7819812   POLYGON ((43.97854 56.32570, 43.98040 56.32666...   
             8310106   POLYGON ((43.95441 56.32301, 43.95252 56.32385...   
             9802449   POLYGON ((43.83789 56.22712, 43.83600 56.22862...   
             10581909  POLYGON ((43.94629 56.25615, 43.94621 56.25746...   
             13108789  POLYGON ((43.94660 56.33597, 43.94660 56.33620...   

                           access                     name description  \
element_type osmid                                                       
way          28501972         NaN  Парк имени А.С. Пушкина         NaN   
             35979423         NaN      Парк имени Кулибина         NaN   
             43052698         NaN                      NaN         NaN   
             48519800  permissive    Ботанический сад ННГУ         NaN   
             54512879         NaN                    Полёт         NaN   
...                           ...                      ...         ...   
relation     7819812          NaN                      NaN         NaN   
             8310106          NaN                      NaN         NaN   
             9802449          NaN                      NaN         NaN   
             10581909         NaN      Сквер Первых маёвок         NaN   
             13108789         NaN                  Стрелка         NaN   

                      tourism  \
element_type osmid              
way          28501972     NaN   
             35979423     NaN   
             43052698     NaN   
             48519800     NaN   
             54512879     NaN   
...                       ...   
relation     7819812      NaN   
             8310106      NaN   
             9802449      NaN   
             10581909     NaN   
             13108789     NaN   

                                                                   nodes  \
element_type osmid                                                         
way          28501972  [313109463, 313109464, 313109465, 420212759, 3...   
             35979423  [1627193723, 1627193731, 1290609521, 420538570...   
             43052698  [539341288, 539341286, 539341290, 539341292, 5...   
             48519800  [616409345, 616409342, 616409343, 616413472, 6...   
             54512879  [1108812771, 1108812770, 1108812774, 388459819...   
...                                                                  ...   
relation     7819812   [[[6566445147, 6566445146, 6566445148, 6566445...   
             8310106   [[[550703162, 5584608335, 5584608331, 55846083...   
             9802449   [[[6620696061, 6620696057, 6620696056, 6620696...   
             10581909  [[[1243300601, 5208854379, 7128173697, 3808121...   
             13108789  [[[259472319, 9853356711, 1711797457, 13135052...   

                             alt_name  leisure  \
element_type osmid                               
way          28501972  Пушкинский сад     park   
             35979423             NaN     park   
             43052698

In [234]:
# Для дальнейшей работы создаём новый геодатафрейм на основе полученного набора данных
gdf_park_nizhny_1500 = park_nizhny_1500["geometry"].to_frame()

In [237]:
# Выгружаем зелёные зоны (парки, сады, стадионы) города из OpenStreetMap
tags = {"leisure":["park", "garden", "stadium"]}

features_park_samara = ox.features.features_from_place("Samara", tags=tags)

In [238]:
features_park_samara

geometry  \
element_type osmid                                                           
node         6076306323                          POINT (50.21805 53.21132)   
             6627842640                          POINT (50.16056 53.21256)   
             6627842641                          POINT (50.16173 53.21285)   
             6627842642                          POINT (50.16164 53.21281)   
             6627842643                          POINT (50.16153 53.21276)   
...                                                                    ...   
relation     7840785     POLYGON ((50.11319 53.20178, 50.11415 53.20100...   
             9154519     POLYGON ((50.10008 53.18538, 50.09833 53.18582...   
             16301429    POLYGON ((50.20678 53.25452, 50.20666 53.25455...   
             16310301    MULTIPOLYGON (((50.16052 53.20406, 50.16058 53...   
             17348651    POLYGON ((50.27494 53.30505, 50.27705 53.30582...   

                        barrier highway              name access  leisure  \
element_type osmid                                                          
node         6076306323     NaN     NaN                PG    yes   garden   
             6627842640     NaN     NaN               NaN    NaN   garden   
             6627842641     NaN     NaN               NaN    NaN   garden   
             6627842642     NaN     NaN               NaN    NaN   garden   
             6627842643     NaN     NaN               NaN    NaN   garden   
...                         ...     ...               ...    ...      ...   
relation     7840785        NaN     NaN    Сквер Устинова    NaN     park   
             9154519        NaN     NaN   Сквер Высоцкого    NaN     park   
             16301429       NaN     NaN  Солнечная поляна    NaN     park   
             16310301       NaN     NaN          парк Мир    NaN     park   
             17348651       NaN     NaN             Салют    NaN  stadium   

                        contact:email contact:facebook contact:instagram  \
element_type osmid                                                         
node         6076306323           NaN              NaN               NaN   
             6627842640           NaN              NaN               NaN   
             6627842641           NaN              NaN               NaN   
             6627842642           NaN              NaN               NaN   
             6627842643           NaN              NaN               NaN   
...                               ...              ...               ...   
relation     7840785              NaN              NaN               NaN   
             9154519              NaN              NaN               NaN   
             16301429             NaN              NaN               NaN   
             16310301             NaN              NaN               NaN   
             17348651             NaN              NaN               NaN   

                        contact:phone  ...         name:ru subject:wikidata  \
element_type osmid                     ...                                    
node         6076306323           NaN  ...             NaN              NaN   
             6627842640           NaN  ...             NaN              NaN   
             6627842641           NaN  ...             NaN              NaN   
             6627842642           NaN  ...             NaN              NaN   
             6627842643           NaN  ...             NaN              NaN   
...                               ...  ...             ...              ...   
relation     7840785              NaN  ...  Сквер Устинова              NaN   
             9154519              NaN  ...             NaN              NaN   
             16301429             NaN  ...             NaN              NaN   
             16310301             NaN  ...             NaN              NaN   
             17348651             NaN  ...             NaN              NaN   

                        subject:

In [239]:
type(features_park_samara)

geopandas.geodataframe.GeoDataFrame

In [241]:
# Переводим координаты в геодатафрейме с зелёными зонами города в проекцию EPSG:32637 (UTM Zone 37N)
park_samara_1500 = features_park_samara.to_crs(32637)
# создаём буферную зону в размере 1500 м вокруг каждого геометрического объекта в наборе
park_samara_1500["geometry"] = park_samara_1500["geometry"].buffer(1500)
# переводим полученные координаты в EPSG:4326 (WGS84)
park_samara_1500 = park_samara_1500.to_crs(4326)

In [242]:
park_samara_1500

geometry  \
element_type osmid                                                           
node         6076306323  POLYGON ((50.24008 53.20922, 50.23963 53.20793...   
             6627842640  POLYGON ((50.18260 53.21047, 50.18215 53.20919...   
             6627842641  POLYGON ((50.18377 53.21076, 50.18332 53.20947...   
             6627842642  POLYGON ((50.18367 53.21072, 50.18322 53.20943...   
             6627842643  POLYGON ((50.18357 53.21066, 50.18312 53.20938...   
...                                                                    ...   
relation     7840785     POLYGON ((50.10001 53.21259, 50.10183 53.21331...   
             9154519     POLYGON ((50.09791 53.17205, 50.09574 53.17225...   
             16301429    POLYGON ((50.18188 53.25903, 50.18238 53.26029...   
             16310301    POLYGON ((50.15004 53.21608, 50.15100 53.21650...   
             17348651    POLYGON ((50.25542 53.29853, 50.25447 53.29967...   

                        barrier highway              name access  leisure  \
element_type osmid                                                          
node         6076306323     NaN     NaN                PG    yes   garden   
             6627842640     NaN     NaN               NaN    NaN   garden   
             6627842641     NaN     NaN               NaN    NaN   garden   
             6627842642     NaN     NaN               NaN    NaN   garden   
             6627842643     NaN     NaN               NaN    NaN   garden   
...                         ...     ...               ...    ...      ...   
relation     7840785        NaN     NaN    Сквер Устинова    NaN     park   
             9154519        NaN     NaN   Сквер Высоцкого    NaN     park   
             16301429       NaN     NaN  Солнечная поляна    NaN     park   
             16310301       NaN     NaN          парк Мир    NaN     park   
             17348651       NaN     NaN             Салют    NaN  stadium   

                        contact:email contact:facebook contact:instagram  \
element_type osmid                                                         
node         6076306323           NaN              NaN               NaN   
             6627842640           NaN              NaN               NaN   
             6627842641           NaN              NaN               NaN   
             6627842642           NaN              NaN               NaN   
             6627842643           NaN              NaN               NaN   
...                               ...              ...               ...   
relation     7840785              NaN              NaN               NaN   
             9154519              NaN              NaN               NaN   
             16301429             NaN              NaN               NaN   
             16310301             NaN              NaN               NaN   
             17348651             NaN              NaN               NaN   

                        contact:phone  ...         name:ru subject:wikidata  \
element_type osmid                     ...                                    
node         6076306323           NaN  ...             NaN              NaN   
             6627842640           NaN  ...             NaN              NaN   
             6627842641           NaN  ...             NaN              NaN   
             6627842642           NaN  ...             NaN              NaN   
             6627842643           NaN  ...             NaN              NaN   
...                               ...  ...             ...              ...   
relation     7840785              NaN  ...  Сквер Устинова              NaN   
             9154519              NaN  ...             NaN              NaN   
             16301429             NaN  ...             NaN              NaN   
             16310301             NaN  ...             NaN              NaN   
             17348651             NaN  ...             NaN              NaN   

                        subject:

In [245]:
# Для дальнейшей работы создаём новый геодатафрейм на основе полученного набора данных
gdf_park_samara_1500 = park_samara_1500["geometry"].to_frame()

In [246]:
type(gdf_park_samara_1500)

geopandas.geodataframe.GeoDataFrame

In [334]:
# В датафрейме с тренировочными данными создаём столбец "green_zone" для указания, попадает ли квартира в зелёную зону
df_train_nodes_copy["green_zone"] = ""

In [335]:
# Создаём геодатафрейм на основе датасета с тренировочными данными
gdf_train = gpd.GeoDataFrame(df_train_nodes_copy, geometry="geometry")

gdf_train

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs nearest_node count_stops  \
0      POINT (444364.7583481302 5896144.765920336)   1376917912           0   
1      POINT (507758.0518276638 4987276.430569851)    533897701           0   
2        POINT (497764.34935612 4990660.299869019)    921918400           0   
3      POINT (450620.75961276994 5896598.90707207)  10828204246           0   
4      POINT (458831.4735939478 5890813.869220274)    597712746           0   
...                                            ...          ...         ...   
8037   POINT (451849.04119317944 5899200.85693531)   1567984170           3   
8038  POINT (497370.9552071012 4991160.3494087905)  11462814570           0   
8039    POINT (502265.426288711 4995470.469169812)   7310019142           0   
8040  POINT (501409.53431823035 4988649.361517621)    295196089           0   
8041  POINT (496263.39146830165 4995082.349866582)  11394107436           0   

     green_zone  
0                
1                
2                
3                
4                
...         ...  
8037             
8038             
8039             
8040             
8041             

[8042 rows x 13 columns]

In [336]:
type(gdf_train)

geopandas.geodataframe.GeoDataFrame

In [337]:
# С помощью метода "within" определяем, находится ли квартира из тренировочного датасета внутри
# зелёной зоны города (полигона)
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in gdf_train.index:
    if gdf_train.at[i, "green_zone"] == "":
        if gdf_train.at[i, "city"] == "Краснодар":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_krasnodar_1500["geometry"]:
                if gdf_train.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_train.at[i, "green_zone"] = is_within

        elif gdf_train.at[i, "city"] == "Нижний Новгород":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_nizhny_1500["geometry"]:
                if gdf_train.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_train.at[i, "green_zone"] = is_within

        elif gdf_train.at[i, "city"] == "Самара":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_samara_1500["geometry"]:
                if gdf_train.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_train.at[i, "green_zone"] = is_within
            
        count_ += 1
        print(f'Проработано: {count_} объектов')
 

#gdf["green_zone"] = gdf["geometry"].apply(
    #lambda point: gdf_park_krasnodar_1500["geometry"].apply(lambda poly:
        #point.within(poly)).any()
#)

Проработано: 1 объектов
Проработано: 2 объектов
Проработано: 3 объектов
Проработано: 4 объектов
Проработано: 5 объектов
Проработано: 6 объектов
Проработано: 7 объектов
Проработано: 8 объектов
Проработано: 9 объектов
Проработано: 10 объектов
Проработано: 11 объектов
Проработано: 12 объектов
Проработано: 13 объектов
Проработано: 14 объектов
Проработано: 15 объектов
Проработано: 16 объектов
Проработано: 17 объектов
Проработано: 18 объектов
Проработано: 19 объектов
Проработано: 20 объектов
Проработано: 21 объектов
Проработано: 22 объектов
Проработано: 23 объектов
Проработано: 24 объектов
Проработано: 25 объектов
Проработано: 26 объектов
Проработано: 27 объектов
Проработано: 28 объектов
Проработано: 29 объектов
Проработано: 30 объектов
Проработано: 31 объектов
Проработано: 32 объектов
Проработано: 33 объектов
Проработано: 34 объектов
Проработано: 35 объектов
Проработано: 36 объектов
Проработано: 37 объектов
Проработано: 38 объектов
Проработано: 39 объектов
Проработано: 40 объектов
Проработа

Проработано: 353 объектов
Проработано: 354 объектов
Проработано: 355 объектов
Проработано: 356 объектов
Проработано: 357 объектов
Проработано: 358 объектов
Проработано: 359 объектов
Проработано: 360 объектов
Проработано: 361 объектов
Проработано: 362 объектов
Проработано: 363 объектов
Проработано: 364 объектов
Проработано: 365 объектов
Проработано: 366 объектов
Проработано: 367 объектов
Проработано: 368 объектов
Проработано: 369 объектов
Проработано: 370 объектов
Проработано: 371 объектов
Проработано: 372 объектов
Проработано: 373 объектов
Проработано: 374 объектов
Проработано: 375 объектов
Проработано: 376 объектов
Проработано: 377 объектов
Проработано: 378 объектов
Проработано: 379 объектов
Проработано: 380 объектов
Проработано: 381 объектов
Проработано: 382 объектов
Проработано: 383 объектов
Проработано: 384 объектов
Проработано: 385 объектов
Проработано: 386 объектов
Проработано: 387 объектов
Проработано: 388 объектов
Проработано: 389 объектов
Проработано: 390 объектов
Проработано:

Проработано: 729 объектов
Проработано: 730 объектов
Проработано: 731 объектов
Проработано: 732 объектов
Проработано: 733 объектов
Проработано: 734 объектов
Проработано: 735 объектов
Проработано: 736 объектов
Проработано: 737 объектов
Проработано: 738 объектов
Проработано: 739 объектов
Проработано: 740 объектов
Проработано: 741 объектов
Проработано: 742 объектов
Проработано: 743 объектов
Проработано: 744 объектов
Проработано: 745 объектов
Проработано: 746 объектов
Проработано: 747 объектов
Проработано: 748 объектов
Проработано: 749 объектов
Проработано: 750 объектов
Проработано: 751 объектов
Проработано: 752 объектов
Проработано: 753 объектов
Проработано: 754 объектов
Проработано: 755 объектов
Проработано: 756 объектов
Проработано: 757 объектов
Проработано: 758 объектов
Проработано: 759 объектов
Проработано: 760 объектов
Проработано: 761 объектов
Проработано: 762 объектов
Проработано: 763 объектов
Проработано: 764 объектов
Проработано: 765 объектов
Проработано: 766 объектов
Проработано:

Проработано: 1053 объектов
Проработано: 1054 объектов
Проработано: 1055 объектов
Проработано: 1056 объектов
Проработано: 1057 объектов
Проработано: 1058 объектов
Проработано: 1059 объектов
Проработано: 1060 объектов
Проработано: 1061 объектов
Проработано: 1062 объектов
Проработано: 1063 объектов
Проработано: 1064 объектов
Проработано: 1065 объектов
Проработано: 1066 объектов
Проработано: 1067 объектов
Проработано: 1068 объектов
Проработано: 1069 объектов
Проработано: 1070 объектов
Проработано: 1071 объектов
Проработано: 1072 объектов
Проработано: 1073 объектов
Проработано: 1074 объектов
Проработано: 1075 объектов
Проработано: 1076 объектов
Проработано: 1077 объектов
Проработано: 1078 объектов
Проработано: 1079 объектов
Проработано: 1080 объектов
Проработано: 1081 объектов
Проработано: 1082 объектов
Проработано: 1083 объектов
Проработано: 1084 объектов
Проработано: 1085 объектов
Проработано: 1086 объектов
Проработано: 1087 объектов
Проработано: 1088 объектов
Проработано: 1089 объектов
П

Проработано: 1357 объектов
Проработано: 1358 объектов
Проработано: 1359 объектов
Проработано: 1360 объектов
Проработано: 1361 объектов
Проработано: 1362 объектов
Проработано: 1363 объектов
Проработано: 1364 объектов
Проработано: 1365 объектов
Проработано: 1366 объектов
Проработано: 1367 объектов
Проработано: 1368 объектов
Проработано: 1369 объектов
Проработано: 1370 объектов
Проработано: 1371 объектов
Проработано: 1372 объектов
Проработано: 1373 объектов
Проработано: 1374 объектов
Проработано: 1375 объектов
Проработано: 1376 объектов
Проработано: 1377 объектов
Проработано: 1378 объектов
Проработано: 1379 объектов
Проработано: 1380 объектов
Проработано: 1381 объектов
Проработано: 1382 объектов
Проработано: 1383 объектов
Проработано: 1384 объектов
Проработано: 1385 объектов
Проработано: 1386 объектов
Проработано: 1387 объектов
Проработано: 1388 объектов
Проработано: 1389 объектов
Проработано: 1390 объектов
Проработано: 1391 объектов
Проработано: 1392 объектов
Проработано: 1393 объектов
П

...

Проработано: 6598 объектов
Проработано: 6599 объектов
Проработано: 6600 объектов
Проработано: 6601 объектов
Проработано: 6602 объектов
Проработано: 6603 объектов
Проработано: 6604 объектов
Проработано: 6605 объектов
Проработано: 6606 объектов
Проработано: 6607 объектов
Проработано: 6608 объектов
Проработано: 6609 объектов
Проработано: 6610 объектов
Проработано: 6611 объектов
Проработано: 6612 объектов
Проработано: 6613 объектов
Проработано: 6614 объектов
Проработано: 6615 объектов
Проработано: 6616 объектов
Проработано: 6617 объектов
Проработано: 6618 объектов
Проработано: 6619 объектов
Проработано: 6620 объектов
Проработано: 6621 объектов
Проработано: 6622 объектов
Проработано: 6623 объектов
Проработано: 6624 объектов
Проработано: 6625 объектов
Проработано: 6626 объектов
Проработано: 6627 объектов
Проработано: 6628 объектов
Проработано: 6629 объектов
Проработано: 6630 объектов
Проработано: 6631 объектов
Проработано: 6632 объектов
Проработано: 6633 объектов
Проработано: 6634 объектов
П

Проработано: 6908 объектов
Проработано: 6909 объектов
Проработано: 6910 объектов
Проработано: 6911 объектов
Проработано: 6912 объектов
Проработано: 6913 объектов
Проработано: 6914 объектов
Проработано: 6915 объектов
Проработано: 6916 объектов
Проработано: 6917 объектов
Проработано: 6918 объектов
Проработано: 6919 объектов
Проработано: 6920 объектов
Проработано: 6921 объектов
Проработано: 6922 объектов
Проработано: 6923 объектов
Проработано: 6924 объектов
Проработано: 6925 объектов
Проработано: 6926 объектов
Проработано: 6927 объектов
Проработано: 6928 объектов
Проработано: 6929 объектов
Проработано: 6930 объектов
Проработано: 6931 объектов
Проработано: 6932 объектов
Проработано: 6933 объектов
Проработано: 6934 объектов
Проработано: 6935 объектов
Проработано: 6936 объектов
Проработано: 6937 объектов
Проработано: 6938 объектов
Проработано: 6939 объектов
Проработано: 6940 объектов
Проработано: 6941 объектов
Проработано: 6942 объектов
Проработано: 6943 объектов
Проработано: 6944 объектов
П

Проработано: 7214 объектов
Проработано: 7215 объектов
Проработано: 7216 объектов
Проработано: 7217 объектов
Проработано: 7218 объектов
Проработано: 7219 объектов
Проработано: 7220 объектов
Проработано: 7221 объектов
Проработано: 7222 объектов
Проработано: 7223 объектов
Проработано: 7224 объектов
Проработано: 7225 объектов
Проработано: 7226 объектов
Проработано: 7227 объектов
Проработано: 7228 объектов
Проработано: 7229 объектов
Проработано: 7230 объектов
Проработано: 7231 объектов
Проработано: 7232 объектов
Проработано: 7233 объектов
Проработано: 7234 объектов
Проработано: 7235 объектов
Проработано: 7236 объектов
Проработано: 7237 объектов
Проработано: 7238 объектов
Проработано: 7239 объектов
Проработано: 7240 объектов
Проработано: 7241 объектов
Проработано: 7242 объектов
Проработано: 7243 объектов
Проработано: 7244 объектов
Проработано: 7245 объектов
Проработано: 7246 объектов
Проработано: 7247 объектов
Проработано: 7248 объектов
Проработано: 7249 объектов
Проработано: 7250 объектов
П

Проработано: 7556 объектов
Проработано: 7557 объектов
Проработано: 7558 объектов
Проработано: 7559 объектов
Проработано: 7560 объектов
Проработано: 7561 объектов
Проработано: 7562 объектов
Проработано: 7563 объектов
Проработано: 7564 объектов
Проработано: 7565 объектов
Проработано: 7566 объектов
Проработано: 7567 объектов
Проработано: 7568 объектов
Проработано: 7569 объектов
Проработано: 7570 объектов
Проработано: 7571 объектов
Проработано: 7572 объектов
Проработано: 7573 объектов
Проработано: 7574 объектов
Проработано: 7575 объектов
Проработано: 7576 объектов
Проработано: 7577 объектов
Проработано: 7578 объектов
Проработано: 7579 объектов
Проработано: 7580 объектов
Проработано: 7581 объектов
Проработано: 7582 объектов
Проработано: 7583 объектов
Проработано: 7584 объектов
Проработано: 7585 объектов
Проработано: 7586 объектов
Проработано: 7587 объектов
Проработано: 7588 объектов
Проработано: 7589 объектов
Проработано: 7590 объектов
Проработано: 7591 объектов
Проработано: 7592 объектов
П

Проработано: 7873 объектов
Проработано: 7874 объектов
Проработано: 7875 объектов
Проработано: 7876 объектов
Проработано: 7877 объектов
Проработано: 7878 объектов
Проработано: 7879 объектов
Проработано: 7880 объектов
Проработано: 7881 объектов
Проработано: 7882 объектов
Проработано: 7883 объектов
Проработано: 7884 объектов
Проработано: 7885 объектов
Проработано: 7886 объектов
Проработано: 7887 объектов
Проработано: 7888 объектов
Проработано: 7889 объектов
Проработано: 7890 объектов
Проработано: 7891 объектов
Проработано: 7892 объектов
Проработано: 7893 объектов
Проработано: 7894 объектов
Проработано: 7895 объектов
Проработано: 7896 объектов
Проработано: 7897 объектов
Проработано: 7898 объектов
Проработано: 7899 объектов
Проработано: 7900 объектов
Проработано: 7901 объектов
Проработано: 7902 объектов
Проработано: 7903 объектов
Проработано: 7904 объектов
Проработано: 7905 объектов
Проработано: 7906 объектов
Проработано: 7907 объектов
Проработано: 7908 объектов
Проработано: 7909 объектов
П

In [338]:
gdf_train

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           NaN          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs nearest_node count_stops  \
0      POINT (444364.7583481302 5896144.765920336)   1376917912           0   
1      POINT (507758.0518276638 4987276.430569851)    533897701           0   
2        POINT (497764.34935612 4990660.299869019)    921918400           0   
3      POINT (450620.75961276994 5896598.90707207)  10828204246           0   
4      POINT (458831.4735939478 5890813.869220274)    597712746           0   
...                                            ...          ...         ...   
8037   POINT (451849.04119317944 5899200.85693531)   1567984170           3   
8038  POINT (497370.9552071012 4991160.3494087905)  11462814570           0   
8039    POINT (502265.426288711 4995470.469169812)   7310019142           0   
8040  POINT (501409.53431823035 4988649.361517621)    295196089           0   
8041  POINT (496263.39146830165 4995082.349866582)  11394107436           0   

     green_zone  
0             1  
1             1  
2             1  
3             1  
4             0  
...         ...  
8037          1  
8038          1  
8039          0  
8040          1  
8041          0  

[8042 rows x 13 columns]

In [340]:
# Создаём колонку апартаментов (отсутствие в квартире кухни) и заполняем пропуски нулями
gdf_train.loc[(gdf_train["area_kitchen"].isna()) | (gdf_train["area_kitchen"] == 0), "is_apart"] = 1
gdf_train = gdf_train.fillna(0)
gdf_train["is_apart"] = gdf_train["is_apart"].astype(int)

/var/folders/hy/pfmkjt294bl40vdb0nfc_y4c0000gn/T/ipykernel_45384/309369035.py:4: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  gdf_train = gdf_train.fillna(0)


In [341]:
gdf_train

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           0.0          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0            True  2473000  POINT (50.16690 53.21170)   
1            True  3733000  POINT (39.09850 45.03890)   
2            True  3445000  POINT (38.97160 45.06940)   
3            True  4458000  POINT (50.26050 53.21640)   
4            True  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037         True  4029000  POINT (50.27850 53.23990)   
8038         True  5263000  POINT (38.96660 45.07390)   
8039        False  2017000  POINT (39.02880 45.11270)   
8040         True  5617000  POINT (39.01790 45.05130)   
8041         True  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs  nearest_node  count_stops  \
0      POINT (444364.7583481302 5896144.765920336)    1376917912            0   
1      POINT (507758.0518276638 4987276.430569851)     533897701            0   
2        POINT (497764.34935612 4990660.299869019)     921918400            0   
3      POINT (450620.75961276994 5896598.90707207)   10828204246            0   
4      POINT (458831.4735939478 5890813.869220274)     597712746            0   
...                                            ...           ...          ...   
8037   POINT (451849.04119317944 5899200.85693531)    1567984170            3   
8038  POINT (497370.9552071012 4991160.3494087905)   11462814570            0   
8039    POINT (502265.426288711 4995470.469169812)    7310019142            0   
8040  POINT (501409.53431823035 4988649.361517621)     295196089            0   
8041  POINT (496263.39146830165 4995082.349866582)   11394107436            0   

      green_zone  is_apart  
0              1         0  
1              1         0  
2              1         0  
3              1         0  
4              0         1  
...          ...       ...  
8037           1         0  
8038           1         0  
8039           0         0  
8040           1         0  
8041           0         0  

[8042 rows x 14 columns]

In [342]:
# Преобразуем колонку балконов в 1 (есть балкон) и 0 (нет балкона)
gdf_train.loc[:, "has_balcony"] = gdf_train.loc[:, "has_balcony"].astype(int)

/var/folders/hy/pfmkjt294bl40vdb0nfc_y4c0000gn/T/ipykernel_45384/2174777982.py:3: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[1 1 1 ... 0 1 1]' has dtype incompatible with bool, please explicitly cast to a compatible dtype first.
  gdf_train.loc[:, "has_balcony"] = gdf_train.loc[:, "has_balcony"].astype(int)


In [343]:
gdf_train

latitude  longitude       city  area  area_kitchen  rooms_num  \
0      53.2117    50.1669     Самара  33.9           8.0          1   
1      45.0389    39.0985  Краснодар  49.8          12.0          2   
2      45.0694    38.9716  Краснодар  45.1          25.1          2   
3      53.2164    50.2605     Самара  70.1          10.0          3   
4      53.1651    50.3842     Самара  34.0           0.0          1   
...        ...        ...        ...   ...           ...        ...   
8037   53.2399    50.2785     Самара  43.0           5.0          2   
8038   45.0739    38.9666  Краснодар  44.9          11.8          1   
8039   45.1127    39.0288  Краснодар  43.1          12.0          1   
8040   45.0513    39.0179  Краснодар  41.1          14.2          1   
8041   45.1092    38.9525  Краснодар  38.9          18.6          1   

      has_balcony    price                   geometry  \
0               1  2473000  POINT (50.16690 53.21170)   
1               1  3733000  POINT (39.09850 45.03890)   
2               1  3445000  POINT (38.97160 45.06940)   
3               1  4458000  POINT (50.26050 53.21640)   
4               1  1295000  POINT (50.38420 53.16510)   
...           ...      ...                        ...   
8037            1  4029000  POINT (50.27850 53.23990)   
8038            1  5263000  POINT (38.96660 45.07390)   
8039            0  2017000  POINT (39.02880 45.11270)   
8040            1  5617000  POINT (39.01790 45.05130)   
8041            1  3729000  POINT (38.95250 45.10920)   

                                      geometry_crs  nearest_node  count_stops  \
0      POINT (444364.7583481302 5896144.765920336)    1376917912            0   
1      POINT (507758.0518276638 4987276.430569851)     533897701            0   
2        POINT (497764.34935612 4990660.299869019)     921918400            0   
3      POINT (450620.75961276994 5896598.90707207)   10828204246            0   
4      POINT (458831.4735939478 5890813.869220274)     597712746            0   
...                                            ...           ...          ...   
8037   POINT (451849.04119317944 5899200.85693531)    1567984170            3   
8038  POINT (497370.9552071012 4991160.3494087905)   11462814570            0   
8039    POINT (502265.426288711 4995470.469169812)    7310019142            0   
8040  POINT (501409.53431823035 4988649.361517621)     295196089            0   
8041  POINT (496263.39146830165 4995082.349866582)   11394107436            0   

      green_zone  is_apart  
0              1         0  
1              1         0  
2              1         0  
3              1         0  
4              0         1  
...          ...       ...  
8037           1         0  
8038           1         0  
8039           0         0  
8040           1         0  
8041           0         0  

[8042 rows x 14 columns]

In [344]:
# Задаём категориальные столбцы и преобразуем их
cat_list = ["city","rooms_num", "has_balcony", "green_zone", "is_apart"]
gdf_train[cat_list] = gdf_train[cat_list].astype("category")

In [345]:
gdf_train.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 8042 entries, 0 to 8041
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   latitude      8042 non-null   float64 
 1   longitude     8042 non-null   float64 
 2   city          8042 non-null   category
 3   area          8042 non-null   float64 
 4   area_kitchen  8042 non-null   float64 
 5   rooms_num     8042 non-null   category
 6   has_balcony   8042 non-null   category
 7   price         8042 non-null   int64   
 8   geometry      8042 non-null   geometry
 9   geometry_crs  8042 non-null   object  
 10  nearest_node  8042 non-null   int64   
 11  count_stops   8042 non-null   int64   
 12  green_zone    8042 non-null   category
 13  is_apart      8042 non-null   category
dtypes: category(5), float64(4), geometry(1), int64(3), object(1)
memory usage: 926.5+ KB


In [346]:
# Сохраняем полученный датафрейм с тренировочными данными в csv-файл
gdf_train.to_csv("gdf_train_v1.csv")

In [300]:
# Копируем тестовый датасет с квартирами в отдельный датафрейм, чтобы в нём собрать ближайшие узлы
# графа OpenStreetMap для координат квартир в городах
df_test_nodes = df_test.copy()

In [301]:
# Для этого добавляем столбец "geometry_crs"
df_test_nodes["geometry_crs"] = ""

df_test_nodes

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry geometry_crs  
0            True  POINT (39.04670 45.01640)               
1           False  POINT (39.04070 45.07290)               
2            True  POINT (39.03250 45.09030)               
3            True  POINT (38.92720 45.10100)               
4            True  POINT (38.90520 45.07510)               
...           ...                        ...          ...  
3438        False  POINT (50.23290 53.21250)               
3439         True  POINT (50.26920 53.27830)               
3440        False  POINT (50.09110 53.19120)               
3441         True  POINT (50.08970 53.19170)               
3442         True  POINT (50.13230 53.20850)               

[3443 rows x 9 columns]

In [302]:
# Переводим координаты квартир в корректные для городов проекции, определённые ранее 
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_test_nodes.index:
    flat_crs = gpd.GeoSeries(df_test_nodes.at[i, "geometry"], crs="EPSG:4326")
    print(f'1 - {flat_crs}')
    if df_test_nodes.at[i, "city"] == "Краснодар":
        df_test_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_1.crs)[0]
        print(f'2 - {flat_crs.to_crs(edges_1.crs)[0]}')
    elif df_test_nodes.at[i, "city"] == "Нижний Новгород":
        df_test_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_2.crs)[0]
    elif df_test_nodes.at[i, "city"] == "Самара":
        df_test_nodes.at[i, "geometry_crs"] = flat_crs.to_crs(edges_3.crs)[0]
        
    count_ += 1
    print(count_)

1 - 0    POINT (39.04670 45.01640)
dtype: geometry
2 - POINT (503679.6241927828 4984773.295640753)
1
1 - 0    POINT (39.04070 45.07290)
dtype: geometry
2 - POINT (503203.7122498007 4991049.523728226)
2
1 - 0    POINT (39.03250 45.09030)
dtype: geometry
2 - POINT (502557.4704863871 4992982.178990674)
3
1 - 0    POINT (38.92720 45.10100)
dtype: geometry
2 - POINT (494272.33584035654 4994172.897198866)
4
1 - 0    POINT (38.90520 45.07510)
dtype: geometry
2 - POINT (492538.07693616446 4991297.484191589)
5
1 - 0    POINT (38.94760 45.09480)
dtype: geometry
2 - POINT (495876.89446352306 4993482.90176939)
6
1 - 0    POINT (39.09430 45.01320)
dtype: geometry
2 - POINT (507430.5757279021 4984421.079421756)
7
1 - 0    POINT (38.95790 45.02300)
dtype: geometry
2 - POINT (496683.2037990508 4985506.275862171)
8
1 - 0    POINT (38.90090 45.08780)
dtype: geometry
2 - POINT (492201.34211650735 4992708.718918909)
9
1 - 0    POINT (38.96380 45.06150)
dtype: geometry
2 - POINT (497149.94010882545 4989782

2 - POINT (503368.89097298594 4991282.895424059)
179
1 - 0    POINT (38.97680 45.05260)
dtype: geometry
2 - POINT (498173.15891788964 4988793.882299301)
180
1 - 0    POINT (38.89870 45.08130)
dtype: geometry
2 - POINT (492027.30942715995 4991986.854993382)
181
1 - 0    POINT (38.97820 45.06820)
dtype: geometry
2 - POINT (498283.86606255884 4990526.832331171)
182
1 - 0    POINT (39.00560 45.09350)
dtype: geometry
2 - POINT (500440.64723019575 4993337.165725943)
183
1 - 0    POINT (39.06000 45.10010)
dtype: geometry
2 - POINT (504720.6764934751 4994072.0901331175)
184
1 - 0    POINT (39.04840 45.08510)
dtype: geometry
2 - POINT (503809.00931738724 4992405.141582435)
185
1 - 0    POINT (39.04890 45.09500)
dtype: geometry
2 - POINT (503847.6938355552 4993504.947172027)
186
1 - 0    POINT (38.90410 45.09380)
dtype: geometry
2 - POINT (492453.95569631277 4993374.95002957)
187
1 - 0    POINT (39.11360 45.03870)
dtype: geometry
2 - POINT (508947.388404916 4987255.770573592)
188
1 - 0    POINT 

2 - POINT (505617.9175238458 4984785.816164184)
331
1 - 0    POINT (38.90650 45.09510)
dtype: geometry
2 - POINT (492642.9704385038 4993519.144877513)
332
1 - 0    POINT (39.05250 45.02770)
dtype: geometry
2 - POINT (504135.808844399 4986028.867100422)
333
1 - 0    POINT (38.90000 45.08930)
dtype: geometry
2 - POINT (492130.7227334982 4992875.439648261)
334
1 - 0    POINT (39.08860 45.03470)
dtype: geometry
2 - POINT (506978.8190426831 4986808.959935871)
335
1 - 0    POINT (38.92870 45.11780)
dtype: geometry
2 - POINT (494391.99626222154 4996039.095030774)
336
1 - 0    POINT (39.06840 44.99620)
dtype: geometry
2 - POINT (505391.3226030533 4982530.543919782)
337
1 - 0    POINT (39.09220 45.01380)
dtype: geometry
2 - POINT (507265.025752908 4984487.541498283)
338
1 - 0    POINT (39.11380 45.04590)
dtype: geometry
2 - POINT (508962.01669524005 4988055.627380151)
339
1 - 0    POINT (38.94400 45.06140)
dtype: geometry
2 - POINT (495591.0598861271 4989772.7239600895)
340
1 - 0    POINT (38.8

2 - POINT (497731.56108846783 4987005.503983694)
535
1 - 0    POINT (39.07580 44.99390)
dtype: geometry
2 - POINT (505974.8333408481 4982275.562262253)
536
1 - 0    POINT (38.95420 45.10100)
dtype: geometry
2 - POINT (496396.6068874907 4994171.339830404)
537
1 - 0    POINT (39.09040 45.03720)
dtype: geometry
2 - POINT (507120.2908844329 4987086.836703562)
538
1 - 0    POINT (38.94560 45.02250)
dtype: geometry
2 - POINT (495714.12627333746 4985451.309243438)
539
1 - 0    POINT (39.03330 45.09060)
dtype: geometry
2 - POINT (502620.409888261 4993015.531319269)
540
1 - 0    POINT (38.95130 45.07380)
dtype: geometry
2 - POINT (496166.62560791324 4991149.851443123)
541
1 - 0    POINT (39.06620 44.99800)
dtype: geometry
2 - POINT (505217.75413384545 4982730.356986521)
542
1 - 0    POINT (39.07320 45.03230)
dtype: geometry
2 - POINT (505766.0373130931 4986541.136952321)
543
1 - 0    POINT (39.06060 45.09930)
dtype: geometry
2 - POINT (504767.94983958505 4993983.2539071655)
544
1 - 0    POINT (

2 - POINT (492679.29942675156 4990897.400264565)
736
1 - 0    POINT (39.00850 45.09840)
dtype: geometry
2 - POINT (500668.78234856186 4993881.522687854)
737
1 - 0    POINT (39.03860 45.09150)
dtype: geometry
2 - POINT (503037.42441886506 4993115.696843132)
738
1 - 0    POINT (39.08450 45.00350)
dtype: geometry
2 - POINT (506659.4870703028 4983342.678596961)
739
1 - 0    POINT (38.98040 45.04250)
dtype: geometry
2 - POINT (498456.36263424443 4987671.816002378)
740
1 - 0    POINT (38.98910 45.05510)
dtype: geometry
2 - POINT (499141.73705829645 4989071.399253654)
741
1 - 0    POINT (38.99100 45.02950)
dtype: geometry
2 - POINT (499291.02641902736 4986227.524199067)
742
1 - 0    POINT (38.95420 45.10100)
dtype: geometry
2 - POINT (496396.6068874907 4994171.339830404)
743
1 - 0    POINT (38.99950 45.09320)
dtype: geometry
2 - POINT (499960.6562913214 4993303.823851325)
744
1 - 0    POINT (38.91030 45.08810)
dtype: geometry
2 - POINT (492941.1104893864 4992741.182507428)
745
1 - 0    POINT 

...

2 - POINT (500424.88832387177 4993659.323276578)
2058
1 - 0    POINT (38.91460 45.01600)
dtype: geometry
2 - POINT (493271.0472410085 4984731.3469053935)
2059
1 - 0    POINT (39.20930 45.01970)
dtype: geometry
2 - POINT (516490.3877998342 4985160.1293714605)
2060
1 - 0    POINT (38.94420 45.01960)
dtype: geometry
2 - POINT (495603.6061202005 4985129.229842309)
2061
1 - 0    POINT (38.91690 45.12040)
dtype: geometry
2 - POINT (493464.18027569953 4996328.814200999)
2062
1 - 0    POINT (39.03480 45.02540)
dtype: geometry
2 - POINT (502741.56021737814 4985772.613557232)
2063
1 - 0    POINT (39.00860 45.06120)
dtype: geometry
2 - POINT (500677.0895924329 4989749.0170510085)
2064
1 - 0    POINT (38.95270 45.07450)
dtype: geometry
2 - POINT (496276.8707344213 4991227.54821972)
2065
1 - 0    POINT (38.90410 45.09380)
dtype: geometry
2 - POINT (492453.95569631277 4993374.95002957)
2066
1 - 0    POINT (39.03760 45.07270)
dtype: geometry
2 - POINT (502959.7051777777 4991027.187928631)
2067
1 - 0 

2 - POINT (498598.5991071407 4989826.897143147)
2239
1 - 0    POINT (38.90960 45.08810)
dtype: geometry
2 - POINT (492886.02439516445 4992741.243820798)
2240
1 - 0    POINT (39.04270 45.07430)
dtype: geometry
2 - POINT (503361.06076449004 4991205.129117768)
2241
1 - 0    POINT (39.02140 45.11370)
dtype: geometry
2 - POINT (501683.30819242087 4995581.378039226)
2242
1 - 0    POINT (38.99790 45.09670)
dtype: geometry
2 - POINT (499834.7665170063 4993692.638002814)
2243
1 - 0    POINT (38.90400 45.09400)
dtype: geometry
2 - POINT (492446.11340311123 4993397.177194257)
2244
1 - 0    POINT (38.98400 45.06640)
dtype: geometry
2 - POINT (498740.412625339 4990326.766154274)
2245
1 - 0    POINT (38.90080 45.08110)
dtype: geometry
2 - POINT (492192.56007751805 4991964.432436053)
2246
1 - 0    POINT (39.01150 45.09100)
dtype: geometry
2 - POINT (500904.9400413415 4993059.491976202)
2247
1 - 0    POINT (39.02910 45.05120)
dtype: geometry
2 - POINT (502291.4815719078 4988638.5086964965)
2248
1 - 0 

2498
1 - 0    POINT (44.04810 56.28640)
dtype: geometry
2499
1 - 0    POINT (44.03910 56.31360)
dtype: geometry
2500
1 - 0    POINT (43.83400 56.21920)
dtype: geometry
2501
1 - 0    POINT (43.84630 56.24890)
dtype: geometry
2502
1 - 0    POINT (43.91850 56.27410)
dtype: geometry
2503
1 - 0    POINT (43.84490 56.33410)
dtype: geometry
2504
1 - 0    POINT (43.92330 56.25770)
dtype: geometry
2505
1 - 0    POINT (43.87580 56.33600)
dtype: geometry
2506
1 - 0    POINT (44.01160 56.31410)
dtype: geometry
2507
1 - 0    POINT (43.87330 56.22640)
dtype: geometry
2508
1 - 0    POINT (43.83270 56.23190)
dtype: geometry
2509
1 - 0    POINT (43.93300 56.30680)
dtype: geometry
2510
1 - 0    POINT (43.93720 56.33390)
dtype: geometry
2511
1 - 0    POINT (43.92630 56.34320)
dtype: geometry
2512
1 - 0    POINT (43.87450 56.26530)
dtype: geometry
2513
1 - 0    POINT (43.86200 56.35010)
dtype: geometry
2514
1 - 0    POINT (43.92110 56.27910)
dtype: geometry
2515
1 - 0    POINT (43.94030 56.32380)
dtype: g

1 - 0    POINT (43.85040 56.23160)
dtype: geometry
2669
1 - 0    POINT (44.00780 56.32070)
dtype: geometry
2670
1 - 0    POINT (43.85570 56.33090)
dtype: geometry
2671
1 - 0    POINT (43.81130 56.30950)
dtype: geometry
2672
1 - 0    POINT (43.83420 56.23830)
dtype: geometry
2673
1 - 0    POINT (43.94480 56.28570)
dtype: geometry
2674
1 - 0    POINT (44.07380 56.30510)
dtype: geometry
2675
1 - 0    POINT (44.07750 56.30350)
dtype: geometry
2676
1 - 0    POINT (44.02620 56.30950)
dtype: geometry
2677
1 - 0    POINT (43.98630 56.31290)
dtype: geometry
2678
1 - 0    POINT (43.99670 56.30550)
dtype: geometry
2679
1 - 0    POINT (43.88200 56.30170)
dtype: geometry
2680
1 - 0    POINT (43.90900 56.27460)
dtype: geometry
2681
1 - 0    POINT (43.94880 56.23520)
dtype: geometry
2682
1 - 0    POINT (44.02190 56.30660)
dtype: geometry
2683
1 - 0    POINT (43.97290 56.30280)
dtype: geometry
2684
1 - 0    POINT (43.98080 56.27570)
dtype: geometry
2685
1 - 0    POINT (43.87500 56.33690)
dtype: geomet

3012
1 - 0    POINT (50.22390 53.20700)
dtype: geometry
3013
1 - 0    POINT (50.23340 53.13660)
dtype: geometry
3014
1 - 0    POINT (50.14810 53.18950)
dtype: geometry
3015
1 - 0    POINT (50.23170 53.25880)
dtype: geometry
3016
1 - 0    POINT (50.28870 53.23610)
dtype: geometry
3017
1 - 0    POINT (50.24570 53.24480)
dtype: geometry
3018
1 - 0    POINT (50.26290 53.24700)
dtype: geometry
3019
1 - 0    POINT (50.14530 53.21560)
dtype: geometry
3020
1 - 0    POINT (50.23100 53.20110)
dtype: geometry
3021
1 - 0    POINT (50.07450 53.15330)
dtype: geometry
3022
1 - 0    POINT (50.16770 53.19700)
dtype: geometry
3023
1 - 0    POINT (50.22030 53.22170)
dtype: geometry
3024
1 - 0    POINT (50.18830 53.20800)
dtype: geometry
3025
1 - 0    POINT (50.22910 53.24110)
dtype: geometry
3026
1 - 0    POINT (50.23230 53.26650)
dtype: geometry
3027
1 - 0    POINT (50.17910 53.24290)
dtype: geometry
3028
1 - 0    POINT (50.12980 53.13610)
dtype: geometry
3029
1 - 0    POINT (50.08340 53.17960)
dtype: g

In [303]:
df_test_nodes

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs  
0       POINT (503679.6241927828 4984773.295640753)  
1       POINT (503203.7122498007 4991049.523728226)  
2       POINT (502557.4704863871 4992982.178990674)  
3      POINT (494272.33584035654 4994172.897198866)  
4      POINT (492538.07693616446 4991297.484191589)  
...                                             ...  
3438  POINT (448773.18043347297 5896184.4664658485)  
3439   POINT (451272.05837237067 5903478.930938232)  
3440    POINT (439273.9042863805 5893925.943418219)  
3441   POINT (439181.07624439197 5893982.753111792)  
3442    POINT (442049.8673390824 5895816.257810241)  

[3443 rows x 9 columns]

In [304]:
df_test_nodes["nearest_node"] = ""

df_test_nodes

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs nearest_node  
0       POINT (503679.6241927828 4984773.295640753)               
1       POINT (503203.7122498007 4991049.523728226)               
2       POINT (502557.4704863871 4992982.178990674)               
3      POINT (494272.33584035654 4994172.897198866)               
4      POINT (492538.07693616446 4991297.484191589)               
...                                             ...          ...  
3438  POINT (448773.18043347297 5896184.4664658485)               
3439   POINT (451272.05837237067 5903478.930938232)               
3440    POINT (439273.9042863805 5893925.943418219)               
3441   POINT (439181.07624439197 5893982.753111792)               
3442    POINT (442049.8673390824 5895816.257810241)               

[3443 rows x 10 columns]

In [305]:
# С помощью библиотеки osmnx ищем ближайшие узлы графа OpenStreetMap для координат
# квартир в каждом городе
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_test_nodes.index:
    if df_test_nodes.at[i, "city"] == "Краснодар":
        df_test_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_krasnodar, df_test_nodes.at[i, "geometry_crs"].x, df_test_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_test_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_test_nodes.at[i, "nearest_node"]}')
    elif df_test_nodes.at[i, "city"] == "Нижний Новгород":
        df_test_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_nizhny_novgorod, df_test_nodes.at[i, "geometry_crs"].x, df_test_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_test_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_test_nodes.at[i, "nearest_node"]}')
    elif df_test_nodes.at[i, "city"] == "Самара":
        df_test_nodes.at[i, "nearest_node"] = ox.distance.nearest_nodes(G_samara, df_test_nodes.at[i, "geometry_crs"].x, df_test_nodes.at[i, "geometry_crs"].y)
        print(f'1 - {df_test_nodes.at[i, "geometry_crs"]}')
        print(f'2 - {df_test_nodes.at[i, "nearest_node"]}')
        
    count_ += 1
    print(count_)

1 - POINT (503679.6241927828 4984773.295640753)
2 - 1234702318
1
1 - POINT (503203.7122498007 4991049.523728226)
2 - 7104549572
2
1 - POINT (502557.4704863871 4992982.178990674)
2 - 7098473514
3
1 - POINT (494272.33584035654 4994172.897198866)
2 - 298719791
4
1 - POINT (492538.07693616446 4991297.484191589)
2 - 11432426761
5
1 - POINT (495876.89446352306 4993482.90176939)
2 - 11191466909
6
1 - POINT (507430.5757279021 4984421.079421756)
2 - 9004386270
7
1 - POINT (496683.2037990508 4985506.275862171)
2 - 3328329543
8
1 - POINT (492201.34211650735 4992708.718918909)
2 - 7592225552
9
1 - POINT (497149.94010882545 4989782.944962472)
2 - 9134755778
10
1 - POINT (492989.5517839214 4986697.906492921)
2 - 1042838683
11
1 - POINT (500692.4444390086 4993348.29705186)
2 - 4578748905
12
1 - POINT (502556.4036700642 4995637.213788512)
2 - 9932028095
13
1 - POINT (492453.83717349736 4993274.969796359)
2 - 11403404123
14
1 - POINT (502426.0496707467 4986794.494719485)
2 - 9227704150
15
1 - POINT (50

1 - POINT (502273.24471221183 4995603.779421547)
2 - 6776782541
124
1 - POINT (492286.3591177075 4991431.0908104675)
2 - 7598130179
125
1 - POINT (502306.42633332073 4990860.284781202)
2 - 9883620231
126
1 - POINT (507688.1300808511 4986476.511031668)
2 - 530182108
127
1 - POINT (501762.5120184408 4993615.117440831)
2 - 10605902218
128
1 - POINT (502194.6508800649 4995414.8995910715)
2 - 6776782541
129
1 - POINT (496551.99378930114 4990538.643088435)
2 - 5141302999
130
1 - POINT (503564.80126450205 4992838.247512256)
2 - 4210190656
131
1 - POINT (492311.9710077466 4993086.287769)
2 - 11414999035
132
1 - POINT (492587.87813674414 4993508.09986009)
2 - 11412132586
133
1 - POINT (497731.56108846783 4987005.503983694)
2 - 9123040821
134
1 - POINT (502888.7402588964 4991293.76845071)
2 - 11554269709
135
1 - POINT (501683.3052526745 4995592.4869939005)
2 - 1084642091
136
1 - POINT (504767.94983958505 4993983.2539071655)
2 - 11586700063
137
1 - POINT (500558.6143603468 4994059.254886177)
2 - 

1 - POINT (495283.8853866418 4989606.311028292)
2 - 295174635
247
1 - POINT (504088.5211011628 4986062.162996466)
2 - 11669259897
248
1 - POINT (493840.97984208993 4995584.137027985)
2 - 7656339684
249
1 - POINT (503290.0752776091 4991482.814132598)
2 - 11554269336
250
1 - POINT (492375.0295875261 4993175.083346056)
2 - 9174506387
251
1 - POINT (503290.0752776091 4991482.814132598)
2 - 11554269336
252
1 - POINT (497288.2372415664 5000225.294260818)
2 - 566593518
253
1 - POINT (492201.5598364716 4992886.461407282)
2 - 11400836787
254
1 - POINT (496538.4485551027 4994582.291752864)
2 - 11394250906
255
1 - POINT (506706.9017120345 4983220.5319665205)
2 - 11730315442
256
1 - POINT (506250.1834645924 4982820.153816364)
2 - 1900121940
257
1 - POINT (507454.1240800143 4984498.8682955755)
2 - 11521206124
258
1 - POINT (502409.5613879182 4988738.531748893)
2 - 8993115131
259
1 - POINT (498173.15891788964 4988793.882299301)
2 - 582636730
260
1 - POINT (492829.6297283376 4984576.304662226)
2 - 58

1 - POINT (500165.23117583187 4993781.509380027)
2 - 11194218812
369
1 - POINT (493390.68375577603 4993718.285340193)
2 - 4045850606
370
1 - POINT (502485.5197910467 4995870.473841073)
2 - 1989847913
371
1 - POINT (504736.57743435045 4993849.923303863)
2 - 11586700189
372
1 - POINT (501611.9177308707 4997936.46245954)
2 - 10604413145
373
1 - POINT (505958.8198822218 4982542.156885771)
2 - 11724697901
374
1 - POINT (502521.9666420866 4983261.942827881)
2 - 8279588547
375
1 - POINT (497049.9634806963 4994904.1933675725)
2 - 7655546610
376
1 - POINT (503703.20402644377 4984873.288200385)
2 - 11694267835
377
1 - POINT (495901.015198074 4994282.729099693)
2 - 11396131729
378
1 - POINT (495927.91511048516 4987128.597387819)
2 - 1545848169
379
1 - POINT (502958.6623821951 4993271.184559822)
2 - 11530460502
380
1 - POINT (503258.92092883284 4990838.483091045)
2 - 9077023979
381
1 - POINT (495337.20337141 4987151.219516717)
2 - 11465319139
382
1 - POINT (505789.5980367041 4986618.919930113)
2 -

1 - POINT (500582.23404463095 4993881.514181713)
2 - 8296339162
491
1 - POINT (503564.813704914 4992816.0297)
2 - 4210190656
492
1 - POINT (505572.9295964212 4982164.111694898)
2 - 11727715506
493
1 - POINT (493417.6233277784 4989330.243884531)
2 - 1178875929
494
1 - POINT (502487.4768645908 4990860.35290338)
2 - 4751258753
495
1 - POINT (506903.4873359806 4983631.765354723)
2 - 11730737299
496
1 - POINT (492642.9704385038 4993519.144877513)
2 - 11412132593
497
1 - POINT (503029.5237231425 4993182.3465641895)
2 - 11530460125
498
1 - POINT (498851.09153256303 4992904.006602104)
2 - 11465115032
499
1 - POINT (503847.6938355552 4993504.947172027)
2 - 4210190664
500
1 - POINT (497112.88247017877 4994870.837671159)
2 - 11383853160
501
1 - POINT (495956.5680004631 4995038.101672364)
2 - 3644594815
502
1 - POINT (504081.64510779787 4984495.820903782)
2 - 2022764250
503
1 - POINT (498332.91008015856 4997436.572034048)
2 - 11459536458
504
1 - POINT (503619.7601648163 4993060.456760001)
2 - 1154

...

1 - POINT (442198.9464926671 5895992.465427008)
2 - 2110811602
2905
1 - POINT (444961.75171021395 5893467.682373834)
2 - 4132589862
2906
1 - POINT (446945.92308090616 5895826.137664574)
2 - 1762473913
2907
1 - POINT (454344.18570543587 5905362.098883367)
2 - 1108240642
2908
1 - POINT (445892.4716080005 5901879.2251477465)
2 - 340162082
2909
1 - POINT (452276.64059826505 5906572.806532522)
2 - 10866446159
2910
1 - POINT (447361.087982017 5900160.553015139)
2 - 249655309
2911
1 - POINT (448072.63820408203 5898706.4203299945)
2 - 1952668077
2912
1 - POINT (443451.2542081357 5895143.045433934)
2 - 7693448930
2913
1 - POINT (453756.3665461531 5907292.492263586)
2 - 10717519415
2914
1 - POINT (446968.23863169324 5893623.017368972)
2 - 11958308373
2915
1 - POINT (451214.4439054064 5898495.267900186)
2 - 3778394258
2916
1 - POINT (446040.78589556774 5896704.077435517)
2 - 7133014506
2917
1 - POINT (452126.80548347987 5895615.661848752)
2 - 664311564
2918
1 - POINT (448168.67744700477 5904468.4

1 - POINT (448797.6004374027 5902192.041656188)
2 - 5817370339
3027
1 - POINT (445219.3056383332 5899606.12313428)
2 - 7201816524
3028
1 - POINT (441784.98771876795 5887764.40875365)
2 - 6857096866
3029
1 - POINT (438742.93043886713 5892642.107122649)
2 - 7414777702
3030
1 - POINT (448892.3891032324 5899209.35140966)
2 - 961876696
3031
1 - POINT (438260.4504093196 5889955.834050463)
2 - 3935537068
3032
1 - POINT (441759.71120407945 5895575.0170338955)
2 - 4120943190
3033
1 - POINT (448167.4254806093 5896369.009910558)
2 - 6775304021
3034
1 - POINT (453945.80635819584 5906901.260649682)
2 - 3711183358
3035
1 - POINT (439852.1880330286 5893150.945828991)
2 - 11752328485
3036
1 - POINT (450237.18649271666 5896958.904574436)
2 - 248292091
3037
1 - POINT (452174.00028477085 5894992.1651340565)
2 - 4258462058
3038
1 - POINT (440126.1621463621 5893681.550349993)
2 - 1451575686
3039
1 - POINT (445788.1174060779 5898564.933252776)
2 - 946252849
3040
1 - POINT (458346.99694747984 5900419.1320999

1 - POINT (435310.3786912988 5883953.3714515185)
2 - 10678021002
3148
1 - POINT (449026.22744245006 5896115.006389898)
2 - 2611446832
3149
1 - POINT (446201.75441110716 5897358.677431)
2 - 7521825626
3150
1 - POINT (452260.83291241416 5905660.6646926645)
2 - 11799963561
3151
1 - POINT (447398.70714255713 5898124.138993052)
2 - 947045471
3152
1 - POINT (447259.5516674301 5897613.89373725)
2 - 946911062
3153
1 - POINT (448511.2257307465 5898523.659298733)
2 - 961876615
3154
1 - POINT (448022.4754694127 5895936.68639962)
2 - 10827371172
3155
1 - POINT (449118.1051529434 5895335.23834246)
2 - 9496198189
3156
1 - POINT (453684.59677610913 5907448.948232985)
2 - 5672922148
3157
1 - POINT (440679.1483168881 5894086.314758502)
2 - 5168673835
3158
1 - POINT (441467.8948684329 5894655.136539533)
2 - 10961736963
3159
1 - POINT (438463.81548974995 5885480.617835542)
2 - 502168561
3160
1 - POINT (444512.9536830574 5883559.94914938)
2 - 9658847777
3161
1 - POINT (442927.7680930581 5896617.875015667)

1 - POINT (448378.1465082058 5902263.318726975)
2 - 945425687
3270
1 - POINT (447905.4569159857 5901734.4260458555)
2 - 945426281
3271
1 - POINT (452174.00028477085 5894992.1651340565)
2 - 4258462058
3272
1 - POINT (436190.3016680769 5888681.238550318)
2 - 8428014115
3273
1 - POINT (439055.0636689629 5889333.728896236)
2 - 429304759
3274
1 - POINT (442900.79286954884 5896595.945752857)
2 - 9471268464
3275
1 - POINT (439525.182660533 5893188.447726226)
2 - 1271394045
3276
1 - POINT (444468.0291702024 5894686.093289669)
2 - 3658661341
3277
1 - POINT (444524.03609700745 5896632.446625957)
2 - 5608060438
3278
1 - POINT (453163.0166700603 5897752.598109683)
2 - 5625531749
3279
1 - POINT (447110.5282909453 5899228.765223681)
2 - 948660078
3280
1 - POINT (454102.01553787786 5899590.299424484)
2 - 507691610
3281
1 - POINT (446150.1595424847 5896335.695575344)
2 - 8823307935
3282
1 - POINT (444632.54897499847 5896775.822326727)
2 - 7146288214
3283
1 - POINT (450660.45047104557 5898500.961663961

1 - POINT (453905.93702588824 5906912.772082458)
2 - 3711183348
3392
1 - POINT (452284.53032842115 5906695.109294028)
2 - 10866446164
3393
1 - POINT (444293.0558324214 5896868.775869325)
2 - 5932754949
3394
1 - POINT (448451.08148544445 5900371.164969542)
2 - 951666408
3395
1 - POINT (452331.060940652 5906683.517556322)
2 - 8904164999
3396
1 - POINT (448047.26672103105 5910444.3590636635)
2 - 457246982
3397
1 - POINT (445439.4033448975 5896087.869200933)
2 - 4193377015
3398
1 - POINT (445466.8128487088 5893806.7910497775)
2 - 4135553460
3399
1 - POINT (448883.0932368317 5899587.722192379)
2 - 962271160
3400
1 - POINT (449906.0073035808 5897852.41071089)
2 - 7669024142
3401
1 - POINT (445302.26408783573 5893441.523709083)
2 - 4132589871
3402
1 - POINT (450310.9805768948 5898916.232118902)
2 - 254375366
3403
1 - POINT (452459.69128305133 5898860.970608703)
2 - 9514989991
3404
1 - POINT (453414.41219920956 5907073.31484533)
2 - 508399514
3405
1 - POINT (438330.38637756126 5885515.70986529

In [306]:
df_test_nodes

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs nearest_node  
0       POINT (503679.6241927828 4984773.295640753)   1234702318  
1       POINT (503203.7122498007 4991049.523728226)   7104549572  
2       POINT (502557.4704863871 4992982.178990674)   7098473514  
3      POINT (494272.33584035654 4994172.897198866)    298719791  
4      POINT (492538.07693616446 4991297.484191589)  11432426761  
...                                             ...          ...  
3438  POINT (448773.18043347297 5896184.4664658485)   1004368928  
3439   POINT (451272.05837237067 5903478.930938232)    596235220  
3440    POINT (439273.9042863805 5893925.943418219)   6163938367  
3441   POINT (439181.07624439197 5893982.753111792)   1991358690  
3442    POINT (442049.8673390824 5895816.257810241)   4196680214  

[3443 rows x 10 columns]

In [311]:
# Проверяем координаты по ближайшему узлу
G_samara.nodes[1004368928]

{'y': 5896170.701154468,
 'x': 448782.7970286313,
 'street_count': 3,
 'lon': 50.2330462,
 'lat': 53.2123772}

In [312]:
# Сохраняем датафрейм с узлами графа OpenStreetMap в csv-файл
df_test_nodes.to_csv("df_test_nodes.csv")

In [313]:
# Копируем полученный датасет с узлами графа OpenStreetMap, чтобы по этим узлам найти количество
# ближайших остановок, находящихся в пешей доступности от квартиры
df_test_nodes_copy = df_test_nodes.copy()

In [314]:
df_test_nodes_copy["count_stops"] = ""
df_test_nodes_copy

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs nearest_node count_stops  
0       POINT (503679.6241927828 4984773.295640753)   1234702318              
1       POINT (503203.7122498007 4991049.523728226)   7104549572              
2       POINT (502557.4704863871 4992982.178990674)   7098473514              
3      POINT (494272.33584035654 4994172.897198866)    298719791              
4      POINT (492538.07693616446 4991297.484191589)  11432426761              
...                                             ...          ...         ...  
3438  POINT (448773.18043347297 5896184.4664658485)   1004368928              
3439   POINT (451272.05837237067 5903478.930938232)    596235220              
3440    POINT (439273.9042863805 5893925.943418219)   6163938367              
3441   POINT (439181.07624439197 5893982.753111792)   1991358690              
3442    POINT (442049.8673390824 5895816.257810241)   4196680214              

[3443 rows x 11 columns]

In [315]:
# С помощью библиотеки networkx находим остановки, находящиеся от квартиры на расстоянии не более,
# чем в 1 км (1000 м).
# Для этого пройдёмся по датасетам (с остановками в городах и с квартирами)
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in df_test_nodes_copy.index:
    if df_test_nodes_copy.at[i, "count_stops"] == "":
        if df_test_nodes_copy.at[i, "city"] == "Краснодар":
            count_stop = 0 # задаём счётчик для увеличения количества найденных остановок на указанном расстоянии
            for j in stops_krasnodar_crs.index:
                try:
                     '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_krasnodar, df_test_nodes_copy.at[i, "nearest_node"], stops_krasnodar_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_test_nodes_copy.at[i, "count_stops"] = count_stop

        elif df_test_nodes_copy.at[i, "city"] == "Нижний Новгород":
            count_stop = 0
            for j in stops_nizhny_crs.index:
                try:
                     '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_nizhny_novgorod, df_test_nodes_copy.at[i, "nearest_node"], stops_nizhny_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_test_nodes_copy.at[i, "count_stops"] = count_stop

        elif df_test_nodes_copy.at[i, "city"] == "Самара":
            count_stop = 0
            for j in stops_samara_crs.index:
                try:
                     '''
                    с помощью библиотеки networkx определяем расстояние между квартирой и городскими остановками
                    по графу OpenStreetMap и сравниваем полученное расстояние с допустимым
                    '''
                    route_length = nx.shortest_path_length(G_samara, df_test_nodes_copy.at[i, "nearest_node"], stops_samara_crs.at[j, "nearest_node"], weight="length")
                    if route_length <= 1000:
                        '''
                        в случае нахождения остановки на допустимом расстоянии
                        увеличиваем количество остановок в счётчике для итерируемой квартиры
                        '''
                        count_stop += 1
                except ValueError:
                    continue
            # обновляем значение количества остановок для итерируемой квартиры
            df_test_nodes_copy.at[i, "count_stops"] = count_stop
        count_ += 1
        print(f'Проработано: {count_} объектов')
    else:
        continue

Проработано: 1 объектов
Проработано: 2 объектов
Проработано: 3 объектов
Проработано: 4 объектов
Проработано: 5 объектов
Проработано: 6 объектов
Проработано: 7 объектов
Проработано: 8 объектов
Проработано: 9 объектов
Проработано: 10 объектов
Проработано: 11 объектов
Проработано: 12 объектов
Проработано: 13 объектов
Проработано: 14 объектов
Проработано: 15 объектов
Проработано: 16 объектов
Проработано: 17 объектов
Проработано: 18 объектов
Проработано: 19 объектов
Проработано: 20 объектов
Проработано: 21 объектов
Проработано: 22 объектов
Проработано: 23 объектов
Проработано: 24 объектов
Проработано: 25 объектов
Проработано: 26 объектов
Проработано: 27 объектов
Проработано: 28 объектов
Проработано: 29 объектов
Проработано: 30 объектов
Проработано: 31 объектов
Проработано: 32 объектов
Проработано: 33 объектов
Проработано: 34 объектов
Проработано: 35 объектов
Проработано: 36 объектов
Проработано: 37 объектов
Проработано: 38 объектов
Проработано: 39 объектов
Проработано: 40 объектов
Проработа

Проработано: 321 объектов
Проработано: 322 объектов
Проработано: 323 объектов
Проработано: 324 объектов
Проработано: 325 объектов
Проработано: 326 объектов
Проработано: 327 объектов
Проработано: 328 объектов
Проработано: 329 объектов
Проработано: 330 объектов
Проработано: 331 объектов
Проработано: 332 объектов
Проработано: 333 объектов
Проработано: 334 объектов
Проработано: 335 объектов
Проработано: 336 объектов
Проработано: 337 объектов
Проработано: 338 объектов
Проработано: 339 объектов
Проработано: 340 объектов
Проработано: 341 объектов
Проработано: 342 объектов
Проработано: 343 объектов
Проработано: 344 объектов
Проработано: 345 объектов
Проработано: 346 объектов
Проработано: 347 объектов
Проработано: 348 объектов
Проработано: 349 объектов
Проработано: 350 объектов
Проработано: 351 объектов
Проработано: 352 объектов
Проработано: 353 объектов
Проработано: 354 объектов
Проработано: 355 объектов
Проработано: 356 объектов
Проработано: 357 объектов
Проработано: 358 объектов
Проработано:

Проработано: 637 объектов
Проработано: 638 объектов
Проработано: 639 объектов
Проработано: 640 объектов
Проработано: 641 объектов
Проработано: 642 объектов
Проработано: 643 объектов
Проработано: 644 объектов
Проработано: 645 объектов
Проработано: 646 объектов
Проработано: 647 объектов
Проработано: 648 объектов
Проработано: 649 объектов
Проработано: 650 объектов
Проработано: 651 объектов
Проработано: 652 объектов
Проработано: 653 объектов
Проработано: 654 объектов
Проработано: 655 объектов
Проработано: 656 объектов
Проработано: 657 объектов
Проработано: 658 объектов
Проработано: 659 объектов
Проработано: 660 объектов
Проработано: 661 объектов
Проработано: 662 объектов
Проработано: 663 объектов
Проработано: 664 объектов
Проработано: 665 объектов
Проработано: 666 объектов
Проработано: 667 объектов
Проработано: 668 объектов
Проработано: 669 объектов
Проработано: 670 объектов
Проработано: 671 объектов
Проработано: 672 объектов
Проработано: 673 объектов
Проработано: 674 объектов
Проработано:

Проработано: 953 объектов
Проработано: 954 объектов
Проработано: 955 объектов
Проработано: 956 объектов
Проработано: 957 объектов
Проработано: 958 объектов
Проработано: 959 объектов
Проработано: 960 объектов
Проработано: 961 объектов
Проработано: 962 объектов
Проработано: 963 объектов
Проработано: 964 объектов
Проработано: 965 объектов
Проработано: 966 объектов
Проработано: 967 объектов
Проработано: 968 объектов
Проработано: 969 объектов
Проработано: 970 объектов
Проработано: 971 объектов
Проработано: 972 объектов
Проработано: 973 объектов
Проработано: 974 объектов
Проработано: 975 объектов
Проработано: 976 объектов
Проработано: 977 объектов
Проработано: 978 объектов
Проработано: 979 объектов
Проработано: 980 объектов
Проработано: 981 объектов
Проработано: 982 объектов
Проработано: 983 объектов
Проработано: 984 объектов
Проработано: 985 объектов
Проработано: 986 объектов
Проработано: 987 объектов
Проработано: 988 объектов
Проработано: 989 объектов
Проработано: 990 объектов
Проработано:

Проработано: 1259 объектов
Проработано: 1260 объектов
Проработано: 1261 объектов
Проработано: 1262 объектов
Проработано: 1263 объектов
Проработано: 1264 объектов
Проработано: 1265 объектов
Проработано: 1266 объектов
Проработано: 1267 объектов
Проработано: 1268 объектов
Проработано: 1269 объектов
Проработано: 1270 объектов
Проработано: 1271 объектов
Проработано: 1272 объектов
Проработано: 1273 объектов
Проработано: 1274 объектов
Проработано: 1275 объектов
Проработано: 1276 объектов
Проработано: 1277 объектов
Проработано: 1278 объектов
Проработано: 1279 объектов
Проработано: 1280 объектов
Проработано: 1281 объектов
Проработано: 1282 объектов
Проработано: 1283 объектов
Проработано: 1284 объектов
Проработано: 1285 объектов
Проработано: 1286 объектов
Проработано: 1287 объектов
Проработано: 1288 объектов
Проработано: 1289 объектов
Проработано: 1290 объектов
Проработано: 1291 объектов
Проработано: 1292 объектов
Проработано: 1293 объектов
Проработано: 1294 объектов
Проработано: 1295 объектов
П

...

Проработано: 2171 объектов
Проработано: 2172 объектов
Проработано: 2173 объектов
Проработано: 2174 объектов
Проработано: 2175 объектов
Проработано: 2176 объектов
Проработано: 2177 объектов
Проработано: 2178 объектов
Проработано: 2179 объектов
Проработано: 2180 объектов
Проработано: 2181 объектов
Проработано: 2182 объектов
Проработано: 2183 объектов
Проработано: 2184 объектов
Проработано: 2185 объектов
Проработано: 2186 объектов
Проработано: 2187 объектов
Проработано: 2188 объектов
Проработано: 2189 объектов
Проработано: 2190 объектов
Проработано: 2191 объектов
Проработано: 2192 объектов
Проработано: 2193 объектов
Проработано: 2194 объектов
Проработано: 2195 объектов
Проработано: 2196 объектов
Проработано: 2197 объектов
Проработано: 2198 объектов
Проработано: 2199 объектов
Проработано: 2200 объектов
Проработано: 2201 объектов
Проработано: 2202 объектов
Проработано: 2203 объектов
Проработано: 2204 объектов
Проработано: 2205 объектов
Проработано: 2206 объектов
Проработано: 2207 объектов
П

Проработано: 2475 объектов
Проработано: 2476 объектов
Проработано: 2477 объектов
Проработано: 2478 объектов
Проработано: 2479 объектов
Проработано: 2480 объектов
Проработано: 2481 объектов
Проработано: 2482 объектов
Проработано: 2483 объектов
Проработано: 2484 объектов
Проработано: 2485 объектов
Проработано: 2486 объектов
Проработано: 2487 объектов
Проработано: 2488 объектов
Проработано: 2489 объектов
Проработано: 2490 объектов
Проработано: 2491 объектов
Проработано: 2492 объектов
Проработано: 2493 объектов
Проработано: 2494 объектов
Проработано: 2495 объектов
Проработано: 2496 объектов
Проработано: 2497 объектов
Проработано: 2498 объектов
Проработано: 2499 объектов
Проработано: 2500 объектов
Проработано: 2501 объектов
Проработано: 2502 объектов
Проработано: 2503 объектов
Проработано: 2504 объектов
Проработано: 2505 объектов
Проработано: 2506 объектов
Проработано: 2507 объектов
Проработано: 2508 объектов
Проработано: 2509 объектов
Проработано: 2510 объектов
Проработано: 2511 объектов
П

Проработано: 2779 объектов
Проработано: 2780 объектов
Проработано: 2781 объектов
Проработано: 2782 объектов
Проработано: 2783 объектов
Проработано: 2784 объектов
Проработано: 2785 объектов
Проработано: 2786 объектов
Проработано: 2787 объектов
Проработано: 2788 объектов
Проработано: 2789 объектов
Проработано: 2790 объектов
Проработано: 2791 объектов
Проработано: 2792 объектов
Проработано: 2793 объектов
Проработано: 2794 объектов
Проработано: 2795 объектов
Проработано: 2796 объектов
Проработано: 2797 объектов
Проработано: 2798 объектов
Проработано: 2799 объектов
Проработано: 2800 объектов
Проработано: 2801 объектов
Проработано: 2802 объектов
Проработано: 2803 объектов
Проработано: 2804 объектов
Проработано: 2805 объектов
Проработано: 2806 объектов
Проработано: 2807 объектов
Проработано: 2808 объектов
Проработано: 2809 объектов
Проработано: 2810 объектов
Проработано: 2811 объектов
Проработано: 2812 объектов
Проработано: 2813 объектов
Проработано: 2814 объектов
Проработано: 2815 объектов
П

Проработано: 3083 объектов
Проработано: 3084 объектов
Проработано: 3085 объектов
Проработано: 3086 объектов
Проработано: 3087 объектов
Проработано: 3088 объектов
Проработано: 3089 объектов
Проработано: 3090 объектов
Проработано: 3091 объектов
Проработано: 3092 объектов
Проработано: 3093 объектов
Проработано: 3094 объектов
Проработано: 3095 объектов
Проработано: 3096 объектов
Проработано: 3097 объектов
Проработано: 3098 объектов
Проработано: 3099 объектов
Проработано: 3100 объектов
Проработано: 3101 объектов
Проработано: 3102 объектов
Проработано: 3103 объектов
Проработано: 3104 объектов
Проработано: 3105 объектов
Проработано: 3106 объектов
Проработано: 3107 объектов
Проработано: 3108 объектов
Проработано: 3109 объектов
Проработано: 3110 объектов
Проработано: 3111 объектов
Проработано: 3112 объектов
Проработано: 3113 объектов
Проработано: 3114 объектов
Проработано: 3115 объектов
Проработано: 3116 объектов
Проработано: 3117 объектов
Проработано: 3118 объектов
Проработано: 3119 объектов
П

Проработано: 3387 объектов
Проработано: 3388 объектов
Проработано: 3389 объектов
Проработано: 3390 объектов
Проработано: 3391 объектов
Проработано: 3392 объектов
Проработано: 3393 объектов
Проработано: 3394 объектов
Проработано: 3395 объектов
Проработано: 3396 объектов
Проработано: 3397 объектов
Проработано: 3398 объектов
Проработано: 3399 объектов
Проработано: 3400 объектов
Проработано: 3401 объектов
Проработано: 3402 объектов
Проработано: 3403 объектов
Проработано: 3404 объектов
Проработано: 3405 объектов
Проработано: 3406 объектов
Проработано: 3407 объектов
Проработано: 3408 объектов
Проработано: 3409 объектов
Проработано: 3410 объектов
Проработано: 3411 объектов
Проработано: 3412 объектов
Проработано: 3413 объектов
Проработано: 3414 объектов
Проработано: 3415 объектов
Проработано: 3416 объектов
Проработано: 3417 объектов
Проработано: 3418 объектов
Проработано: 3419 объектов
Проработано: 3420 объектов
Проработано: 3421 объектов
Проработано: 3422 объектов
Проработано: 3423 объектов
П

In [316]:
# Сохраняем датафрейм с количеством найденных остановок в csv-файл
df_test_nodes_copy.to_csv("df_test_stops.csv")

In [317]:
# В датафрейме с тестовыми данными создаём столбец "green_zone" для указания, попадает ли квартира в зелёную зону
df_test_nodes_copy["green_zone"] = ""

In [318]:
# Создаём геодатафрейм на основе датасета с тестовыми данными
gdf_test = gpd.GeoDataFrame(df_test_nodes_copy, geometry="geometry")

gdf_test

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs nearest_node count_stops  \
0       POINT (503679.6241927828 4984773.295640753)   1234702318           0   
1       POINT (503203.7122498007 4991049.523728226)   7104549572           0   
2       POINT (502557.4704863871 4992982.178990674)   7098473514           0   
3      POINT (494272.33584035654 4994172.897198866)    298719791           0   
4      POINT (492538.07693616446 4991297.484191589)  11432426761           0   
...                                             ...          ...         ...   
3438  POINT (448773.18043347297 5896184.4664658485)   1004368928           1   
3439   POINT (451272.05837237067 5903478.930938232)    596235220           0   
3440    POINT (439273.9042863805 5893925.943418219)   6163938367           1   
3441   POINT (439181.07624439197 5893982.753111792)   1991358690           1   
3442    POINT (442049.8673390824 5895816.257810241)   4196680214           2   

     green_zone  
0                
1                
2                
3                
4                
...         ...  
3438             
3439             
3440             
3441             
3442             

[3443 rows x 12 columns]

In [320]:
# С помощью метода "within" определяем, находится ли квартира из тренировочного датасета внутри
# зелёной зоны города (полигона)
count_ = 0 # задаём счётчик для проверки количества проработанных объектов

for i in gdf_test.index:
    if gdf_test.at[i, "green_zone"] == "":
        if gdf_test.at[i, "city"] == "Краснодар":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_krasnodar_1500["geometry"]:
                if gdf_test.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_test.at[i, "green_zone"] = is_within

        elif gdf_test.at[i, "city"] == "Нижний Новгород":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_nizhny_1500["geometry"]:
                if gdf_test.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_test.at[i, "green_zone"] = is_within

        elif gdf_test.at[i, "city"] == "Самара":
            is_within = 0 # изначально присваиваем искомому значению резльтат "ноль" (0)
            for poly in gdf_park_samara_1500["geometry"]:
                if gdf_test.at[i, "geometry"].within(poly):
                    is_within = 1 # в случае, если квартира лежит в заданном полигоне, переопределяем переменную на значение "единица" (1)
            # обновляем значение "зелёной зоны" для итерируемой квартиры
            gdf_test.at[i, "green_zone"] = is_within
            
        count_ += 1
        print(f'Проработано: {count_} объектов')


#gdf["green_zone"] = gdf["geometry"].apply(
    #lambda point: gdf_park_krasnodar_1500["geometry"].apply(lambda poly:
        #point.within(poly)).any()
#)

Проработано: 1 объектов
Проработано: 2 объектов
Проработано: 3 объектов
Проработано: 4 объектов
Проработано: 5 объектов
Проработано: 6 объектов
Проработано: 7 объектов
Проработано: 8 объектов
Проработано: 9 объектов
Проработано: 10 объектов
Проработано: 11 объектов
Проработано: 12 объектов
Проработано: 13 объектов
Проработано: 14 объектов
Проработано: 15 объектов
Проработано: 16 объектов
Проработано: 17 объектов
Проработано: 18 объектов
Проработано: 19 объектов
Проработано: 20 объектов
Проработано: 21 объектов
Проработано: 22 объектов
Проработано: 23 объектов
Проработано: 24 объектов
Проработано: 25 объектов
Проработано: 26 объектов
Проработано: 27 объектов
Проработано: 28 объектов
Проработано: 29 объектов
Проработано: 30 объектов
Проработано: 31 объектов
Проработано: 32 объектов
Проработано: 33 объектов
Проработано: 34 объектов
Проработано: 35 объектов
Проработано: 36 объектов
Проработано: 37 объектов
Проработано: 38 объектов
Проработано: 39 объектов
Проработано: 40 объектов
Проработа

Проработано: 359 объектов
Проработано: 360 объектов
Проработано: 361 объектов
Проработано: 362 объектов
Проработано: 363 объектов
Проработано: 364 объектов
Проработано: 365 объектов
Проработано: 366 объектов
Проработано: 367 объектов
Проработано: 368 объектов
Проработано: 369 объектов
Проработано: 370 объектов
Проработано: 371 объектов
Проработано: 372 объектов
Проработано: 373 объектов
Проработано: 374 объектов
Проработано: 375 объектов
Проработано: 376 объектов
Проработано: 377 объектов
Проработано: 378 объектов
Проработано: 379 объектов
Проработано: 380 объектов
Проработано: 381 объектов
Проработано: 382 объектов
Проработано: 383 объектов
Проработано: 384 объектов
Проработано: 385 объектов
Проработано: 386 объектов
Проработано: 387 объектов
Проработано: 388 объектов
Проработано: 389 объектов
Проработано: 390 объектов
Проработано: 391 объектов
Проработано: 392 объектов
Проработано: 393 объектов
Проработано: 394 объектов
Проработано: 395 объектов
Проработано: 396 объектов
Проработано:

Проработано: 716 объектов
Проработано: 717 объектов
Проработано: 718 объектов
Проработано: 719 объектов
Проработано: 720 объектов
Проработано: 721 объектов
Проработано: 722 объектов
Проработано: 723 объектов
Проработано: 724 объектов
Проработано: 725 объектов
Проработано: 726 объектов
Проработано: 727 объектов
Проработано: 728 объектов
Проработано: 729 объектов
Проработано: 730 объектов
Проработано: 731 объектов
Проработано: 732 объектов
Проработано: 733 объектов
Проработано: 734 объектов
Проработано: 735 объектов
Проработано: 736 объектов
Проработано: 737 объектов
Проработано: 738 объектов
Проработано: 739 объектов
Проработано: 740 объектов
Проработано: 741 объектов
Проработано: 742 объектов
Проработано: 743 объектов
Проработано: 744 объектов
Проработано: 745 объектов
Проработано: 746 объектов
Проработано: 747 объектов
Проработано: 748 объектов
Проработано: 749 объектов
Проработано: 750 объектов
Проработано: 751 объектов
Проработано: 752 объектов
Проработано: 753 объектов
Проработано:

Проработано: 1081 объектов
Проработано: 1082 объектов
Проработано: 1083 объектов
Проработано: 1084 объектов
Проработано: 1085 объектов
Проработано: 1086 объектов
Проработано: 1087 объектов
Проработано: 1088 объектов
Проработано: 1089 объектов
Проработано: 1090 объектов
Проработано: 1091 объектов
Проработано: 1092 объектов
Проработано: 1093 объектов
Проработано: 1094 объектов
Проработано: 1095 объектов
Проработано: 1096 объектов
Проработано: 1097 объектов
Проработано: 1098 объектов
Проработано: 1099 объектов
Проработано: 1100 объектов
Проработано: 1101 объектов
Проработано: 1102 объектов
Проработано: 1103 объектов
Проработано: 1104 объектов
Проработано: 1105 объектов
Проработано: 1106 объектов
Проработано: 1107 объектов
Проработано: 1108 объектов
Проработано: 1109 объектов
Проработано: 1110 объектов
Проработано: 1111 объектов
Проработано: 1112 объектов
Проработано: 1113 объектов
Проработано: 1114 объектов
Проработано: 1115 объектов
Проработано: 1116 объектов
Проработано: 1117 объектов
П

Проработано: 1437 объектов
Проработано: 1438 объектов
Проработано: 1439 объектов
Проработано: 1440 объектов
Проработано: 1441 объектов
Проработано: 1442 объектов
Проработано: 1443 объектов
Проработано: 1444 объектов
Проработано: 1445 объектов
Проработано: 1446 объектов
Проработано: 1447 объектов
Проработано: 1448 объектов
Проработано: 1449 объектов
Проработано: 1450 объектов
Проработано: 1451 объектов
Проработано: 1452 объектов
Проработано: 1453 объектов
Проработано: 1454 объектов
Проработано: 1455 объектов
Проработано: 1456 объектов
Проработано: 1457 объектов
Проработано: 1458 объектов
Проработано: 1459 объектов
Проработано: 1460 объектов
Проработано: 1461 объектов
Проработано: 1462 объектов
Проработано: 1463 объектов
Проработано: 1464 объектов
Проработано: 1465 объектов
Проработано: 1466 объектов
Проработано: 1467 объектов
Проработано: 1468 объектов
Проработано: 1469 объектов
Проработано: 1470 объектов
Проработано: 1471 объектов
Проработано: 1472 объектов
Проработано: 1473 объектов
П

Проработано: 1805 объектов
Проработано: 1806 объектов
Проработано: 1807 объектов
Проработано: 1808 объектов
Проработано: 1809 объектов
Проработано: 1810 объектов
Проработано: 1811 объектов
Проработано: 1812 объектов
Проработано: 1813 объектов
Проработано: 1814 объектов
Проработано: 1815 объектов
Проработано: 1816 объектов
Проработано: 1817 объектов
Проработано: 1818 объектов
Проработано: 1819 объектов
Проработано: 1820 объектов
Проработано: 1821 объектов
Проработано: 1822 объектов
Проработано: 1823 объектов
Проработано: 1824 объектов
Проработано: 1825 объектов
Проработано: 1826 объектов
Проработано: 1827 объектов
Проработано: 1828 объектов
Проработано: 1829 объектов
Проработано: 1830 объектов
Проработано: 1831 объектов
Проработано: 1832 объектов
Проработано: 1833 объектов
Проработано: 1834 объектов
Проработано: 1835 объектов
Проработано: 1836 объектов
Проработано: 1837 объектов
Проработано: 1838 объектов
Проработано: 1839 объектов
Проработано: 1840 объектов
Проработано: 1841 объектов
П

Проработано: 2172 объектов
Проработано: 2173 объектов
Проработано: 2174 объектов
Проработано: 2175 объектов
Проработано: 2176 объектов
Проработано: 2177 объектов
Проработано: 2178 объектов
Проработано: 2179 объектов
Проработано: 2180 объектов
Проработано: 2181 объектов
Проработано: 2182 объектов
Проработано: 2183 объектов
Проработано: 2184 объектов
Проработано: 2185 объектов
Проработано: 2186 объектов
Проработано: 2187 объектов
Проработано: 2188 объектов
Проработано: 2189 объектов
Проработано: 2190 объектов
Проработано: 2191 объектов
Проработано: 2192 объектов
Проработано: 2193 объектов
Проработано: 2194 объектов
Проработано: 2195 объектов
Проработано: 2196 объектов
Проработано: 2197 объектов
Проработано: 2198 объектов
Проработано: 2199 объектов
Проработано: 2200 объектов
Проработано: 2201 объектов
Проработано: 2202 объектов
Проработано: 2203 объектов
Проработано: 2204 объектов
Проработано: 2205 объектов
Проработано: 2206 объектов
Проработано: 2207 объектов
Проработано: 2208 объектов
П

Проработано: 2490 объектов
Проработано: 2491 объектов
Проработано: 2492 объектов
Проработано: 2493 объектов
Проработано: 2494 объектов
Проработано: 2495 объектов
Проработано: 2496 объектов
Проработано: 2497 объектов
Проработано: 2498 объектов
Проработано: 2499 объектов
Проработано: 2500 объектов
Проработано: 2501 объектов
Проработано: 2502 объектов
Проработано: 2503 объектов
Проработано: 2504 объектов
Проработано: 2505 объектов
Проработано: 2506 объектов
Проработано: 2507 объектов
Проработано: 2508 объектов
Проработано: 2509 объектов
Проработано: 2510 объектов
Проработано: 2511 объектов
Проработано: 2512 объектов
Проработано: 2513 объектов
Проработано: 2514 объектов
Проработано: 2515 объектов
Проработано: 2516 объектов
Проработано: 2517 объектов
Проработано: 2518 объектов
Проработано: 2519 объектов
Проработано: 2520 объектов
Проработано: 2521 объектов
Проработано: 2522 объектов
Проработано: 2523 объектов
Проработано: 2524 объектов
Проработано: 2525 объектов
Проработано: 2526 объектов
П

Проработано: 2840 объектов
Проработано: 2841 объектов
Проработано: 2842 объектов
Проработано: 2843 объектов
Проработано: 2844 объектов
Проработано: 2845 объектов
Проработано: 2846 объектов
Проработано: 2847 объектов
Проработано: 2848 объектов
Проработано: 2849 объектов
Проработано: 2850 объектов
Проработано: 2851 объектов
Проработано: 2852 объектов
Проработано: 2853 объектов
Проработано: 2854 объектов
Проработано: 2855 объектов
Проработано: 2856 объектов
Проработано: 2857 объектов
Проработано: 2858 объектов
Проработано: 2859 объектов
Проработано: 2860 объектов
Проработано: 2861 объектов
Проработано: 2862 объектов
Проработано: 2863 объектов
Проработано: 2864 объектов
Проработано: 2865 объектов
Проработано: 2866 объектов
Проработано: 2867 объектов
Проработано: 2868 объектов
Проработано: 2869 объектов
Проработано: 2870 объектов
Проработано: 2871 объектов
Проработано: 2872 объектов
Проработано: 2873 объектов
Проработано: 2874 объектов
Проработано: 2875 объектов
Проработано: 2876 объектов
П

Проработано: 3201 объектов
Проработано: 3202 объектов
Проработано: 3203 объектов
Проработано: 3204 объектов
Проработано: 3205 объектов
Проработано: 3206 объектов
Проработано: 3207 объектов
Проработано: 3208 объектов
Проработано: 3209 объектов
Проработано: 3210 объектов
Проработано: 3211 объектов
Проработано: 3212 объектов
Проработано: 3213 объектов
Проработано: 3214 объектов
Проработано: 3215 объектов
Проработано: 3216 объектов
Проработано: 3217 объектов
Проработано: 3218 объектов
Проработано: 3219 объектов
Проработано: 3220 объектов
Проработано: 3221 объектов
Проработано: 3222 объектов
Проработано: 3223 объектов
Проработано: 3224 объектов
Проработано: 3225 объектов
Проработано: 3226 объектов
Проработано: 3227 объектов
Проработано: 3228 объектов
Проработано: 3229 объектов
Проработано: 3230 объектов
Проработано: 3231 объектов
Проработано: 3232 объектов
Проработано: 3233 объектов
Проработано: 3234 объектов
Проработано: 3235 объектов
Проработано: 3236 объектов
Проработано: 3237 объектов
П

In [324]:
gdf_test

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           NaN          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs nearest_node count_stops  \
0       POINT (503679.6241927828 4984773.295640753)   1234702318           0   
1       POINT (503203.7122498007 4991049.523728226)   7104549572           0   
2       POINT (502557.4704863871 4992982.178990674)   7098473514           0   
3      POINT (494272.33584035654 4994172.897198866)    298719791           0   
4      POINT (492538.07693616446 4991297.484191589)  11432426761           0   
...                                             ...          ...         ...   
3438  POINT (448773.18043347297 5896184.4664658485)   1004368928           1   
3439   POINT (451272.05837237067 5903478.930938232)    596235220           0   
3440    POINT (439273.9042863805 5893925.943418219)   6163938367           1   
3441   POINT (439181.07624439197 5893982.753111792)   1991358690           1   
3442    POINT (442049.8673390824 5895816.257810241)   4196680214           2   

     green_zone  
0             1  
1             1  
2             1  
3             1  
4             1  
...         ...  
3438          1  
3439          1  
3440          1  
3441          1  
3442          1  

[3443 rows x 12 columns]

In [332]:
# Создаём колонку апартаментов (отсутствие в квартире кухни) и заполняем пропуски нулями
gdf_test.loc[(gdf_test["area_kitchen"].isna()) | (gdf_test["area_kitchen"] == 0), "is_apart"] = 1
gdf_test = gdf_test.fillna(0)
gdf_test["is_apart"] = gdf_test["is_apart"].astype(int)

gdf_test

latitude  longitude       city   area  area_kitchen  rooms_num  \
0      45.0164    39.0467  Краснодар   67.1           0.0          2   
1      45.0729    39.0407  Краснодар   84.1          15.1          3   
2      45.0903    39.0325  Краснодар   34.9          10.0          1   
3      45.1010    38.9272  Краснодар   31.1           8.8          1   
4      45.0751    38.9052  Краснодар   22.9           3.0          1   
...        ...        ...        ...    ...           ...        ...   
3438   53.2125    50.2329     Самара   31.0           6.0          1   
3439   53.2783    50.2692     Самара   56.6           6.2          3   
3440   53.1912    50.0911     Самара   39.0          10.0          0   
3441   53.1917    50.0897     Самара  148.9          13.8          4   
3442   53.2085    50.1323     Самара   49.4           9.4          2   

      has_balcony                   geometry  \
0            True  POINT (39.04670 45.01640)   
1           False  POINT (39.04070 45.07290)   
2            True  POINT (39.03250 45.09030)   
3            True  POINT (38.92720 45.10100)   
4            True  POINT (38.90520 45.07510)   
...           ...                        ...   
3438        False  POINT (50.23290 53.21250)   
3439         True  POINT (50.26920 53.27830)   
3440        False  POINT (50.09110 53.19120)   
3441         True  POINT (50.08970 53.19170)   
3442         True  POINT (50.13230 53.20850)   

                                       geometry_crs  nearest_node  \
0       POINT (503679.6241927828 4984773.295640753)    1234702318   
1       POINT (503203.7122498007 4991049.523728226)    7104549572   
2       POINT (502557.4704863871 4992982.178990674)    7098473514   
3      POINT (494272.33584035654 4994172.897198866)     298719791   
4      POINT (492538.07693616446 4991297.484191589)   11432426761   
...                                             ...           ...   
3438  POINT (448773.18043347297 5896184.4664658485)    1004368928   
3439   POINT (451272.05837237067 5903478.930938232)     596235220   
3440    POINT (439273.9042863805 5893925.943418219)    6163938367   
3441   POINT (439181.07624439197 5893982.753111792)    1991358690   
3442    POINT (442049.8673390824 5895816.257810241)    4196680214   

      count_stops  green_zone  is_apart  
0               0           1         1  
1               0           1         0  
2               0           1         0  
3               0           1         0  
4               0           1         1  
...           ...         ...       ...  
3438            1           1         0  
3439            0           1         0  
3440            1           1         0  
3441            1           1         0  
3442            2           1         0  

[3443 rows x 13 columns]

In [347]:
# Преобразуем колонку балконов в 1 (есть балкон) и 0 (нет балкона)
gdf_test.loc[:, "has_balcony"] = gdf_test.loc[:, "has_balcony"].astype(int)

/var/folders/hy/pfmkjt294bl40vdb0nfc_y4c0000gn/T/ipykernel_45384/3658070666.py:3: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[1 0 1 ... 0 1 1]' has dtype incompatible with bool, please explicitly cast to a compatible dtype first.
  gdf_test.loc[:, "has_balcony"] = gdf_test.loc[:, "has_balcony"].astype(int)


In [348]:
# Задаём категориальные столбцы и преобразуем их
cat_list = ["city","rooms_num", "has_balcony", "green_zone", "is_apart"]
gdf_test[cat_list] = gdf_test[cat_list].astype("category")

In [349]:
gdf_test.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 3443 entries, 0 to 3442
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   latitude      3443 non-null   float64 
 1   longitude     3443 non-null   float64 
 2   city          3443 non-null   category
 3   area          3443 non-null   float64 
 4   area_kitchen  3443 non-null   float64 
 5   rooms_num     3443 non-null   category
 6   has_balcony   3443 non-null   category
 7   geometry      3443 non-null   geometry
 8   geometry_crs  3443 non-null   object  
 9   nearest_node  3443 non-null   int64   
 10  count_stops   3443 non-null   int64   
 11  green_zone    3443 non-null   category
 12  is_apart      3443 non-null   category
dtypes: category(5), float64(4), geometry(1), int64(2), object(1)
memory usage: 388.8+ KB


In [350]:
# Сохраняем полученный датафрейм с тестовыми данными в csv-файл
gdf_test.to_csv("gdf_test_v1.csv")

In [375]:
# Считываем сохранённые данные
gdf_train = pd.read_csv("gdf_train_v1.csv", index_col=[0])
gdf_test = pd.read_csv("gdf_test_v1.csv", index_col=[0])

gdf_train["geometry"] = gdf_train["geometry"].apply(wkt.loads)
gdf_test["geometry"] = gdf_test["geometry"].apply(wkt.loads)

gdf_train = gpd.GeoDataFrame(gdf_train, geometry="geometry", crs=4326)
gdf_test = gpd.GeoDataFrame(gdf_test, geometry="geometry", crs=4326)

In [376]:
# Удаляем ненужные столбцы
drop_list = ["latitude", "longitude", "geometry_crs", "nearest_node"]

gdf_train = gdf_train.drop(drop_list, axis=1)
gdf_test = gdf_test.drop(drop_list, axis=1)

gdf_train.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 8042 entries, 0 to 8041
Data columns (total 10 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   city          8042 non-null   object  
 1   area          8042 non-null   float64 
 2   area_kitchen  8042 non-null   float64 
 3   rooms_num     8042 non-null   int64   
 4   has_balcony   8042 non-null   int64   
 5   price         8042 non-null   int64   
 6   geometry      8042 non-null   geometry
 7   count_stops   8042 non-null   int64   
 8   green_zone    8042 non-null   int64   
 9   is_apart      8042 non-null   int64   
dtypes: float64(2), geometry(1), int64(6), object(1)
memory usage: 691.1+ KB


In [377]:
# Формируем категориальные столбцы заново
cat_data = ["city", "rooms_num", "has_balcony", "green_zone", "is_apart"]
num_data = ["area", "area_kitchen", "count_stops"]

In [378]:
# Преобразуем категориальные столбцы
gdf_train[cat_data] = gdf_train[cat_data].astype("category")
gdf_test[cat_data] = gdf_test[cat_data].astype("category")

In [382]:
gdf_test.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 3443 entries, 0 to 3442
Data columns (total 9 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   city          3443 non-null   category
 1   area          3443 non-null   float64 
 2   area_kitchen  3443 non-null   float64 
 3   rooms_num     3443 non-null   category
 4   has_balcony   3443 non-null   category
 5   geometry      3443 non-null   geometry
 6   count_stops   3443 non-null   int64   
 7   green_zone    3443 non-null   category
 8   is_apart      3443 non-null   category
dtypes: category(5), float64(2), geometry(1), int64(1)
memory usage: 152.1 KB


In [384]:
gdf_train.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 8042 entries, 0 to 8041
Data columns (total 10 columns):
 #   Column        Non-Null Count  Dtype   
---  ------        --------------  -----   
 0   city          8042 non-null   category
 1   area          8042 non-null   float64 
 2   area_kitchen  8042 non-null   float64 
 3   rooms_num     8042 non-null   category
 4   has_balcony   8042 non-null   category
 5   price         8042 non-null   int64   
 6   geometry      8042 non-null   geometry
 7   count_stops   8042 non-null   int64   
 8   green_zone    8042 non-null   category
 9   is_apart      8042 non-null   category
dtypes: category(5), float64(2), geometry(1), int64(2)
memory usage: 417.1 KB


In [385]:
# Разбиваем данные для обучения
gdf_train, gdf_valid = train_test_split(gdf_train, test_size=0.25, random_state=101)

In [386]:
# Формируем наборы для обучения.
# Разделяем исходные данные (gdf_train) на признаки (features) и целевую переменную (target).
# Признаки создаём путём удаления столбцов "price" и "geometry", а целевой столбец оставляем только "price"
features_train = gdf_train.drop(["price", "geometry"], axis=1)
target_train = gdf_train["price"]

# В валидационном наборе данных также создаём набор признаков без столбца "price" и сохраняем целевую
# переменную "price", чтобы после обучения модели можно было проверить её качество 
features_valid = gdf_valid.drop(["price", "geometry"], axis=1)
target_valid = gdf_valid["price"]

# Удаляем столбец "geometry" для тестовых данных (здесь цена нам неизвестна, мы должны её определить)
features_test = gdf_test.drop(["geometry"], axis=1)

print("Train =", features_train.shape, target_train.shape)
print("Valid =", features_valid.shape, target_valid.shape)
print("Test  =", features_test.shape)

Train = (6031, 8) (6031,)
Valid = (2011, 8) (2011,)
Test  = (3443, 8)


In [388]:
# Задаём пул данных для catboost
train_data = Pool(data=features_train, label=target_train, cat_features=cat_features)
val_data = Pool(data=features_valid, label=target_valid, cat_features=cat_features)

In [389]:
# Задаём параметры модели
param = {
        'eval_metric': 'RMSE',
        'loss_function': 'RMSE',
        'iterations':1000,
        'random_state':101,
        'use_best_model':True,
        'logging_level': 'Silent',
        'learning_rate': 0.01,
        'depth': 12,
    }

In [390]:
# Обучаем модель
model = CatBoostRegressor(**param)
model.fit(train_data, eval_set=val_data, early_stopping_rounds=100)

In [393]:
# Смотрим результат метрики
rmse = root_mean_squared_error(target_valid, model.predict(features_valid))
rmse

2382060.2090795306

In [394]:
# Смотрим важность признаков от catboost
# Видно, что основной вклад в стоимость кваритиры вносит её площадь
feat_importances = model.get_feature_importance(prettified=True)
feat_importances

Feature Id  Importances
0          area    59.440608
1  area_kitchen    13.852113
2          city    12.330684
3     rooms_num     7.056841
4   count_stops     2.875937
5    green_zone     2.642063
6   has_balcony     1.795978
7      is_apart     0.005778

In [395]:
# Делаем предсказание
predict = model.predict(features_test)

In [398]:
# Создаём новый датафрейм с предсказанными данными и индексируем его по индексам тестовых данных в "gdf_test"
df_test_sub = pd.Series(predict, index=gdf_test.index)
df_test_sub.name = "price"

In [401]:
# Сохраняем результат с предсказанными ценами на квартиры в csv-файл
df_test_sub.to_csv("sub_v1.csv")